# 1. 모델의 개요

### 1.1   문제해결 사항 
* 시도별 공용 충전기 설치 현황(2018년.08) 기준으로 전기자동차 충전소가 서울시와 제주도에 집중되어 있는 것을 알 수 있습니다.

* 전남지역 전기차 충전소 설치 현황(20년 4월 기준)을 살펴보면 전남지역의 대도시에 전기차 충전소가 편중되어 있는 것을 확인할 수 있었고, 이에 따라 광양시는 전기자동차 보급 확대 지원에 따른 여러 정책을 시행하고 있습니다.

* 따라서 AiDL팀은 광양시 정책에 따른 전기 자동차 충전기 추가 설치 최적화 입지를 선정하기 위해서 다음과 같은 계획 수립으로 프로젝트를 진행하여 나갔습니다.



# 2. 분석 내용 및 절차

### 분석 흐름도
2.1 각 데이터 전처리  
2.2 학습테이블 만들기 위한 함수 생성  
2.3 매핑  
2.4 K-Means clustering를 이용한 군집화 & 최종 위치 선정

## 2.1 각 데이터 전처리

제공된 데이터들 활용해서 전기차 충전소를 설치하는 데에 적합한 곳을 선정하여 테이블 통합

In [2]:
import pathlib
import numpy as np
import pandas as pd
import geopandas as gpd
from geopandas import GeoDataFrame
import matplotlib.pyplot as plt
import shapely
from shapely.geometry import Polygon, LineString, Point
from folium.plugins import HeatMap
import math
import warnings
warnings.filterwarnings(action='ignore')
import folium

import sklearn.cluster
from sklearn.cluster import KMeans

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
%cd /content/drive/My\ Drive/compas2020/data

/content/drive/My Drive/compas2020/data


In [5]:
owner_land = gpd.read_file('14.광양시_소유지정보.geojson')
gyboundary = gpd.read_file('20.광양시_행정경계(읍면동).geojson')

chargingStation_raw = pd.read_csv('01.광양시_충전기설치현황.csv')
parkingLot_raw = pd.read_csv('02.광양시_주차장_공간정보.csv')
campsite_raw = pd.read_csv('05.광양시_대중집합시설_야영장.csv')
buildinfo = gpd.read_file("15.광양시_건물정보.geojson")
CulPys_raw = gpd.read_file('25.광양시_도시계획(공공문화체육시설).geojson')
traf_parkingLot_raw = gpd.read_file('26.광양시_도시계획(교통시설).geojson')

### 2.1.1 <05.광양시_대중집합시설_야영장.csv>

1) lon, lat가지고 geometry컬럼 만들기  
2) '14.광양시_소유지정보.geojson'데이터를 바탕으로 야영지 면적을 구하기 (컬럼명 : DGM_AR)  
3) cateogory컬럼 추가  
4) 컬럼명 변경 (소유주체(공공/민간) --> 소유주체)  
5) 주차면수 컬럼 추가 --> 주차장법 시행령: 부설주차장의 설치대상 시설물 종류 및 설치기준에 따라 계산

In [ ]:
campsite_raw['geometry'] = campsite_raw.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)
owner_list= np.array([owner_land.토지면적[j]  for i in range(len(campsite_raw)) for j in range(len(owner_land)) if campsite_raw.geometry[i].within(owner_land.geometry[j])==True ])
campsite_raw['DGM_AR']=owner_list
campsite_raw['category'] = '야영장'
campsite_raw.rename(columns={"소유주체(공공/민간)":"소유주체"}, inplace=True)
campsite_raw['주차면수'] = (campsite_raw['DGM_AR']/300).astype(int)
campsite_raw

In [ ]:
campsite_raw.to_csv('광양시_대중집합시설_야영장_전처리.csv', index=False, encoding='cp949')

### 2.1.2 <02.광양시_주차장_공간정보.csv>

1) lon, lat가지고 geometry만들기  
2) 컬럼명 변경 (면적 --> DGM_AR)  
3) cateogory 컬럼 추가  
4) 소유지 컬럼 추가  

In [ ]:
parkingLot_raw['geometry'] = parkingLot_raw.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)
parkingLot_raw.rename(columns={"면적":"DGM_AR"}, inplace=True)
parkingLot_raw['category'] = '주차장'
parkingLot_owner_list= np.array([owner_land.소유구분명[j] for i in range(len(parkingLot_raw.geometry)) for j in range(len(owner_land.geometry)) if parkingLot_raw.geometry[i].within(owner_land.geometry[j])==True])
parkingLot_raw['소유주체'] = parkingLot_owner_list
parkingLot_raw

In [ ]:
parkingLot_raw.to_csv('광양시_주차장_공간정보_전처리.csv', index=False, encoding='cp949')

### 2.1.3 <26.광양시_도시계획(교통시설).geojson>

1) '주차'관련된 데이터만 추출  
2) 면적이 0인 곳은 제외  
3) geometry를 이용해 lon, lat컬럼을 만들고, geometry의 Multipoligon형태를 Point로 변경   
4) category 컬럼 추가  
5) 소유자 컬럼 추가  
6) 주차면수계산

In [ ]:
#'주차'관련된 데이터만 추출  
traf_parkingLot_raw=traf_parkingLot_raw[traf_parkingLot_raw['DGM_NM'].str.contains('주차')]

#면적이 0인 곳은 제외
drop_index = traf_parkingLot_raw[traf_parkingLot_raw['DGM_AR']==0].index
traf_parkingLot_raw = traf_parkingLot_raw.drop(drop_index)

#geometry를 이용해 lon, lat컬럼을 만들고, geometry의 Multipoligon형태를 Point로 변경
traf_parkingLot_raw['lon']=traf_parkingLot_raw['geometry'].centroid.x  #multipoligon형태여서 중심값 추출
traf_parkingLot_raw['lat']=traf_parkingLot_raw['geometry'].centroid.y
traf_parkingLot_raw['geometry'] = traf_parkingLot_raw.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

#category컬럼 추가
traf_parkingLot_raw['category'] = '주차장'

traf_parkingLot_raw.reset_index(drop=True,inplace=True)

#소유자 컬럼 추가
traf_parkingLot_raw['소유주체'] = np.nan
for i in range(len(traf_parkingLot_raw)):
    for j in range(len(owner_land)):
        if traf_parkingLot_raw.geometry[i].within(owner_land.geometry[j]) == True:
            traf_parkingLot_raw['소유주체'][i]=owner_land.소유구분명[j]

traf_parkingLot_raw

In [ ]:
traf_parkingLot_raw.to_csv('광양시_도시계획(교통시설)_전처리(주차면수계산 전).csv', index=False, encoding='cp949')

"광양시_도시계획(교통시설)_전처리.csv"의 주차면수를 계산하기 위해 앞에서 전처리 해놓은 "광양시_주차장_공간정보_전처리.csv"를 이용한다

1)‘02.광양시_주차장_공간정보_전처리.csv에서 'DGM_AR'컬럼과	'주차면수'컬럼을 이용해 면적/주차면수 비를 알아냄.

2) 앞에서 구한 전체 면적/주차면수 비를 통해 '26.광양시_도시계획(교통시설)_전처리csv’에 주차면수를 계산하여 '주차면수' 컬럼 추가

In [ ]:
final_parkinglot = pd.read_csv('광양시_주차장_공간정보_전처리.csv')

parking_area = final_parkinglot['DGM_AR']
s = set()
for i in parking_area:
    if str(i) == "nan":
        pass
    else:
        z = len(str(int(i)))
        s.add(z)
print(s)    #면적 area 크기 자릿수 확인

head =[]

#index 0~3까지는 각 면적의 자릿수 고려 + 같은 앞자리 별 개수, 4~7까지는 각 면적의 자릿수 고려+ 같은 앞자리 계산 값 들의 sum 
for i in range(len(s)+4):
    head.append([0,0,0,0,0,0,0,0,0,0])
print(head)

In [ ]:
parking_count = final_parkinglot['주차면수']

# n = 면적/주차면수 
def count_parkinglot(x, y):
    n = round(x/y,0)
    return n

def head_index(num1, num2, x, y):
  #각각의 n값과, 개수 추가
    for i in range(10):
        if int(x) ==i:
            head[num1][i]+=1
            head[num2][i] +=y

count =0 
for i in parking_area:
    if str(i) == "nan" or str(parking_count[count])== "nan":
        pass
    else:
        if len(str(int(i))) == 2:
            num=count_parkinglot(i, parking_count[count])
            head_index(0, 4, str(int(i))[0], num)
        elif len(str(int(i))) == 3:
            num=count_parkinglot(i, parking_count[count])
            head_index(1, 5, str(int(i))[0], num)
        elif len(str(int(i))) == 4:
            num=count_parkinglot(i, parking_count[count])
            head_index(2, 6, str(int(i))[0], num)
        elif len(str(int(i))) == 5:
            num=count_parkinglot(i, parking_count[count])
            head_index(3, 7, str(int(i))[0], num)
    count+=1
head

In [ ]:
_count =0       #같은 앞자리 별 개수
_count1=3       #같은 앞자리 계산 값 들의 sum 
head2 =[]

for i in range(4):
    head2.append([0,0,0,0,0,0,0,0,0,0])

for i in head[4:8]:
    for j in range(10):
        if head[_count][j]!=0:
            head2[_count][j]=round(i[j]/head[_count][j],0)
    _count+=1
    _count1+=1

head2

In [ ]:
plan_parkinglot = pd.read_csv('광양시_도시계획(교통시설)_전처리(주차면수계산 전).csv', encoding='CP949')

plan_area = plan_parkinglot['DGM_AR']
s = set()
for i in plan_area :
    if str(i) == "nan":
        pass
    else:
        z = len(str(int(i)))
        s.add(z)
s

In [ ]:
final = []

def count_parkinglot(x, y):
    for k in range(10):
        if int(str(x)[0]) == k:
            n = round(int(x)/y[k],0)
            final.append(n)

for i in plan_area :
    if str(i) == "nan" :
        final.append(None)
    else:
        if len(str(int(i))) == 3:
            num=count_parkinglot(i, head2[1])
        elif len(str(int(i))) == 4:
            num=count_parkinglot(i, head2[2])
        elif len(str(int(i))) == 5:
            num=count_parkinglot(i, head2[3])
    count+=1

plan_parkinglot['주차면수']= final
plan_parkinglot['주차면수'].unique()
plan_parkinglot

In [ ]:
plan_parkinglot.to_csv('광양시_도시계획(교통시설)_전처리.csv', index=False, encoding='cp949')

### 2.1.4 <15.광양시_건물정보.geojson>

<15.광양시_건물정보> 데이터에서 <세부용도명>을 기준으로 아래에 해당하는 데이터를 추린 후 각각 전처리하고 합침  
1)아파트, 다가구주택, 다세대주택, 공동주택, 다중주택  
2)기타공공시설, 동사무소, 공공시설, 공공업무시설  
3)대학교, 대학, 쇼핑센터, 관광호텔, 호텔, 주차장  
4)기타문화및집회시설, 도서관, 종합병원,휴게소 

### 1) 각 항목별로 전처리

#### (1) 아파트, 다가구주택, 다세대주택, 공동주택, 다중주택  
공공데이터포털에서 다운받은 <전라남도 광양시 공동주택 현황_20200929.csv> 데이터를 활용하여 각 주택에 대한 세대수를 통해 주차면수를 계산

In [ ]:
공동주택현황 = pd.read_csv("전라남도 광양시 공동주택 현황_20200929.csv")

In [ ]:
#세대수를 동수로 나누어 한 건물당 세대수를 구함
공동주택현황['건물당 세대수'] = 공동주택현황['세대수']/공동주택현황['동수']
공동주택현황 = 공동주택현황.astype({'건물당 세대수':'int'})
공동주택현황

In [ ]:
#건물정보 데이터와 지번을 가지고 매칭시키기 위해 위치컬럼에서 읍,면,동을 제외
address = []
for i in range(len(공동주택현황)):
    address.append(공동주택현황['위치'][i].split(" ")[1:])
print(address)

In [ ]:
# 아파트

아파트 = buildinfo[buildinfo['세부용도명']=='아파트']
아파트.reset_index(drop=True,inplace=True)

#아파트의 지번과 address의 값이 동일할 경우 공동주택현황의 건물당 세대수를 아파트의 세대수 컬럼에 추가
아파트['세대수'] = np.nan
for i in range(len(아파트)):
    for j in range(len(address)):
        for k in range(len(address[j])):
            if 아파트['지번'][i] == address[j][k]:
                아파트['세대수'][i] = 공동주택현황['건물당 세대수'][j]
                
아파트 = 아파트[아파트['세대수'].notnull()]
아파트.reset_index(drop=True,inplace=True)
아파트

<주택건설기준 등에 관한 규정> 제 27조  
주차면수 = 전용면적 X (세대수/75)  
(전용면적 102m^2로 가정)

다만, 전용면적 60m^2이상일 경우 세대 당 주차면수가 1이상이어야 함

In [ ]:
아파트['주차면수'] = np.nan

for i in range(len(아파트)):
    if 102*(아파트['세대수'][i]/75) < 아파트['세대수'][i]:   #구한 세대수가 실제 세대수보다 적을 경우 주차면수를 세대수와 동일하게 함
        아파트['주차면수'][i] = 아파트['세대수'][i]
    else:
        아파트['주차면수'][i] = 102*(아파트['세대수'][i]/75)
아파트.drop(['세대수'], axis='columns', inplace=True)
아파트['주차면수']=round(아파트['주차면수'],0)               #소수 첫 째 자리에서 반올림
아파트

In [ ]:
#다중주택
다중주택 = buildinfo[buildinfo['세부용도명']=='다중주택']
다중주택.reset_index(drop=True,inplace=True)
다중주택

시설면적에 따른 주차면수 계산  
50m^2 < 시설면적 < 150m^2 인 경우 --> 1대  
시설면적 > 150m^ 인 경우--> 1 + (연면적 - 150)/100

In [ ]:
다중주택['주차면수'] = np.nan
for i in range(len(다중주택)):
    if 다중주택['건물연면적'][i] < 150:
        다중주택['주차면수'][i] = 1
    else:
        다중주택['주차면수'][i] = 1 + (다중주택['건물연면적'][i] - 150)/100
다중주택['주차면수']=round(다중주택['주차면수'],0)
다중주택

In [ ]:
#다가구주택 & 다세대주택 & 공동주택
다가구_다세대_공동 = buildinfo[buildinfo['세부용도명'].isin(['다세대주택', '다가구주택', '공동주택'])]
다가구_다세대_공동.reset_index(drop=True,inplace=True)
다가구_다세대_공동

In [ ]:
#다가구,다세대,공동주택 지번과 address의 값이 동일할 경우 공동주택현황의 건물당 세대수를 다가구_다세대_공동 테이블의 세대수 컬럼에 추가

다가구_다세대_공동['세대수'] = np.nan
for i in range(len(다가구_다세대_공동)):
    for j in range(len(address)):
        for k in range(len(address[j])):
            if 다가구_다세대_공동['지번'][i] == address[j][k]:
                다가구_다세대_공동['세대수'][i] = 공동주택현황['건물당 세대수'][j]
                
다가구_다세대_공동 = 다가구_다세대_공동[다가구_다세대_공동['세대수'].notnull()]
다가구_다세대_공동.reset_index(drop=True,inplace=True)
다가구_다세대_공동

<주택건설기준 등에 관한 규정> 제 27조  
주차면수 = 전용면적 X (세대수/95)  
(전용면적 60m^2로 가정)

다만, 전용면적 60m^2이하일 경우 세대 당 주차면수가 0.7대이상이어야 함

In [ ]:
다가구_다세대_공동['주차면수'] = np.nan

#구한 세대수가 실제 세대수보다 적을 경우 세대수에 0.7을 곱한값을 주차면수로 따짐
for i in range(len(다가구_다세대_공동)):
    if 60*(다가구_다세대_공동['세대수'][i]/95) < 다가구_다세대_공동['세대수'][i] * 0.7:    
        다가구_다세대_공동['주차면수'][i] = 다가구_다세대_공동['세대수'][i] * 0.7               
    else:
        다가구_다세대_공동['주차면수'][i] = 60*(다가구_다세대_공동['세대수'][i]/95)       
다가구_다세대_공동['주차면수']=round(다가구_다세대_공동['주차면수'],0)
다가구_다세대_공동.drop(['세대수'], axis='columns', inplace=True)
다가구_다세대_공동

In [ ]:
#아파트, 다중주택, 다가구_다세대_공동 데이터프레임을 "주거"라는 이름의 데이터프레임으로 합치기
주거 = pd.concat([아파트, 다중주택, 다가구_다세대_공동], ignore_index=True)
주거

In [ ]:
#category컬럼 & 소유주체 컬럼 추가

주거['category'] = '주거'
주거['lon']=주거['geometry'].centroid.x  #multipoligon형태여서 중심값 추출
주거['lat']=주거['geometry'].centroid.y
주거['geometry'] = 주거.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

주거['소유주체'] = np.nan
for i in range(len(주거)):
    for j in range(len(owner_land)):
        if 주거.geometry[i].within(owner_land.geometry[j]) == True:
            주거['소유주체'][i]=owner_land.소유구분명[j]


#"항목1" csv파일로 저장
주거.to_csv("항목1.csv", index=False, encoding='cp949')

#### (2) 기타공공시설, 동사무소, 공공시설, 공공업무시설  

기타공공시설, 동사무소, 공공시설, 공공업무시설 --> 주요용도명이 모두 '제1종근린생활시설'

<부설주차장의 설치대상 시설물 종류 및 설치기준> 중 시설물 3번으로 계산

![image-2.png](attachment:image-2.png)

In [ ]:
항목2 = buildinfo[buildinfo['세부용도명'].isin(['기타공공시설','동사무소','공공시설','공공업무시설'])]
항목2.reset_index(drop=True,inplace=True)

항목2['주차면수'] = round(항목2['건물연면적'] / 200, 0)

항목2['category'] = '공공시설'
항목2['lon']=항목2['geometry'].centroid.x  #multipoligon형태여서 중심값 추출
항목2['lat']=항목2['geometry'].centroid.y
항목2['geometry'] = 항목2.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

항목2['소유주체'] = np.nan
for i in range(len(항목2)):
    for j in range(len(owner_land)):
        if 항목2.geometry[i].within(owner_land.geometry[j]) == True:
            항목2['소유주체'][i]=owner_land.소유구분명[j]

In [ ]:
항목2.to_csv("항목2.csv", index=False, encoding='cp949')

#### (3) 대학교, 대학, 쇼핑센터, 관광호텔, 호텔, 주차장  

![image-2.png](attachment:image-2.png)![image-3.png](attachment:image-3.png)![image.png](attachment:image.png)

In [ ]:
항목3 = buildinfo[buildinfo['세부용도명'].isin(['대학교','대학', '쇼핑센터', '관광호텔', '호텔'])]
항목3.reset_index(drop=True,inplace=True)
항목3['주차면수'] = 0

for i in range(len(항목3)):
    if 항목3['세부용도명'][i]=='대학교':
        항목3['주차면수'][i] = round(항목3['건물연면적'][i]/300)   #10번 문항으로 계산
    elif 항목3['세부용도명'][i]=='대학':
        항목3['주차면수'][i] = round(항목3['건물연면적'][i]/300)   #10번 문항으로 계산
    elif 항목3['세부용도명'][i]=='쇼핑센터':
        항목3['주차면수'][i] = round(항목3['건물연면적'][i]/150)   #2번 문항으로 계산
    elif 항목3['세부용도명'][i]=='관광호텔':
        항목3['주차면수'][i] = round(항목3['건물연면적'][i]/200)   #3번 문항으로 계산
    elif 항목3['세부용도명'][i]=='호텔':
        항목3['주차면수'][i] = round(항목3['건물연면적'][i]/200)   #3번 문항으로 계산

In [ ]:
#세부용도가 주차장인 경우 <광양시_주차장_공간정보_전처리>데이터를 활용하여 계산

final_parkinglot = pd.read_csv('광양시_주차장_공간정보_전처리.csv')
building = gpd.read_file('15.광양시_건물정보.geojson')

parkinglot = building[building['세부용도명']=='주차장']

#주차장 면적의 자릿수를 구해서 s에 넣음
parking_area = final_parkinglot['DGM_AR']
s = set()
for i in parking_area:
    if str(i) == "nan":
        pass
    else:
        z = len(str(int(i)))
        s.add(z)
print(s)    

head =[]

#index 0~3까지는 각 면적의 자릿수 고려 + 같은 앞자리 별 개수, 4~7까지는 각 면적의 자릿수 고려+ 같은 앞자리 계산 값 들의 sum 
for i in range(len(s)+4):
    head.append([0,0,0,0,0,0,0,0,0,0])
print(head) #10X8 형태의 배열


In [ ]:
parking_count = final_parkinglot['주차면수']

# n = 면적//주차면수 
def count_parkinglot(x, y):
    n = (x//y)
    return n

def head_index(num1, num2, x, y):
  #각각의 n값과, 개수 추가
    for i in range(10):
        if int(x) ==i:
            head[num1][i]+=1
            head[num2][i] +=y

count =0 
for i in parking_area:
    if str(i) == "nan" or str(parking_count[count])== "nan":
        pass
    else:
        if len(str(int(i))) == 2:
            num=count_parkinglot(i, parking_count[count])
            head_index(0, 4, str(int(i))[0], num)
        elif len(str(int(i))) == 3:
            num=count_parkinglot(i, parking_count[count])
            head_index(1, 5, str(int(i))[0], num)
        elif len(str(int(i))) == 4:
            num=count_parkinglot(i, parking_count[count])
            head_index(2, 6, str(int(i))[0], num)
        elif len(str(int(i))) == 5:
            num=count_parkinglot(i, parking_count[count])
            head_index(3, 7, str(int(i))[0], num)
    count+=1

In [ ]:
_count =0
_count1=3

head2 =[]

for i in range(4):
    head2.append([0,0,0,0,0,0,0,0,0,0])

for i in head[4:8]:
    for j in range(10):
        if head[_count][j]!=0:
            head2[_count][j]=i[j]//head[_count][j]
    _count+=1
    _count1+=1

In [ ]:
parkinglot_area = parkinglot['건물건축면적']
s = set()
for i in parkinglot_area:
    if str(i) == "nan":
        pass
    else:
        z = len(str(int(i)))
        s.add(z)

count =0 
sum=0
for i in parkinglot_area:
    if int(len(str(int(i))))==2:
        sum+=round(int(i)/11.728,0)
        count +=1

final = []
def count_parkinglot(x, y):
    for k in range(10):
        if int(str(x)[0]) == k:
            if int(y[k]) == 0:
                if len(str(int(x)))==2:
                    final.append(6)
                elif len(str(int(x)))==3:
                    final.append(17)
            else:
                n = int(x)//y[k]
                final.append(n)

for i in parkinglot_area:
    if str(i) == "nan":
        final.append(None)
    else:
        if len(str(int(i))) == 2:
            num=count_parkinglot(i, head2[0])
        elif len(str(int(i))) == 3:
            num=count_parkinglot(i, head2[1])
    count+=1
    
parkinglot['주차면수']= final

In [ ]:
항목3['category'] = np.nan
for i in range(len(항목3)):
    if 항목3['세부용도명'][i] == '주차장':
        항목3['category'][i] = '주차장'
    elif (항목3['세부용도명'][i] == '대학교') or (항목3['세부용도명'][i] == '대학'):
        항목3['category'][i] = '대학교'
    elif 항목3['세부용도명'][i] == '쇼핑센터':
        항목3['category'][i] = '쇼핑센터'
    else:
        항목3['category'][i] = '호텔'

항목3['lon']=항목3['geometry'].centroid.x  #multipoligon형태여서 중심값 추출
항목3['lat']=항목3['geometry'].centroid.y
항목3['geometry'] = 항목3.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

항목3['소유주체'] = np.nan
for i in range(len(항목3)):
    for j in range(len(owner_land)):
        if 항목3.geometry[i].within(owner_land.geometry[j]) == True:
            항목3['소유주체'][i]=owner_land.소유구분명[j]
            
항목3

In [ ]:
항목3.to_csv("항목4.csv", index=False, encoding='cp949')

#### (4) 기타문화및집회시설, 도서관, 종합병원,휴게소

In [ ]:
항목4 = buildinfo[buildinfo['세부용도명'].isin(['휴게소','기타문화및집회시설', '도서관', '종합병원'])]
항목4.reset_index(drop=True,inplace=True)
항목4['주차면수'] = 0

#각 용도에 따라 주차면수 계산
for i in range(len(항목4)):
    if 항목4['주요용도명'][i] == '문화및집회시설': #2번 문항으로 계산
        num = 항목4['건물연면적'][i]//150
        항목4['주차면수'][i] = round(num,0) 
    elif 항목4['주요용도명'][i] == '교육연구시설' : #10번 문항으로 계산
        num = 항목4['건물연면적'][i]//300
        항목4['주차면수'][i] = round(num,0)
    elif 항목4['주요용도명'][i] == '관광휴게시설' : #10번 문항으로 계산
        num = 항목4['건물연면적'][i]//300
        항목4['주차면수'][i] = round(num,0)
    else:   #2번 문항으로 계산(의료시설 1개)
        num = 항목4['건물연면적'][i]//150 
        항목4['주차면수'][i] = round(num,0)

In [ ]:
항목4['category'] = np.nan
for i in range(len(항목4)):
    if 항목4['세부용도명'][i] == '휴게소':
        항목4['category'][i] = '휴게소'
    elif 항목4['세부용도명'][i] == '기타문화및집회시설':
        항목4['category'][i] = '기타문화및집회시설'
    elif 항목4['세부용도명'][i] == '도서관':
        항목4['category'][i] = '도서관'
    else:
        항목4['category'][i] = '종합병원'
        

항목4['lon']=항목4['geometry'].centroid.x  #multipoligon형태여서 중심값 추출
항목4['lat']=항목4['geometry'].centroid.y
항목4['geometry'] = 항목4.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

항목4['소유주체'] = np.nan
for i in range(len(항목4)):
    for j in range(len(owner_land)):
        if 항목4.geometry[i].within(owner_land.geometry[j]) == True:
            항목4['소유주체'][i]=owner_land.소유구분명[j]
            
항목4

In [ ]:
항목4.to_csv("항목4.csv", index=False, encoding='cp949')

### 2) 건물정보 전체 합치고 필요없는 컬럼 삭제

In [ ]:
항목1 = pd.read_csv("항목1.csv", encoding='utf-8')
항목2 = pd.read_csv("항목2.csv",encoding='utf-8')
항목3 = pd.read_csv("항목3.csv",encoding='utf-8')
항목4 = pd.read_csv("항목4.csv",encoding='utf-8')

building = pd.concat([항목1, 항목2,항목3, 항목4], ignore_index = True)
building = building[['건물건축면적', 'lon','lat','geometry', 'category', '주차면수', '소유주체']]
building.rename(columns={"건물건축면적":"area"}, inplace=True)

building.to_csv("광양시_건물정보_전처리.csv", index=False, encoding='cp949')

## 2.2 학습테이블 만들기 위한 함수 생성 

1) 완속충전기 설치가능 여부를 계산하기 위한 전처리  
2) 인구분포 & 자동차 등록현황  
3) 학습테이블을 리턴하는 함수 생성  
4) 리턴된 테이블 표준화  

### 2.2.1 완속충전기 설치가능 여부를 계산하기 위한 전처리

In [ ]:
gyboundary = gpd.read_file('20.광양시_행정경계(읍면동).geojson')

chargingStation_raw = pd.read_csv('01.광양시_충전기설치현황.csv')
CulPys_raw = gpd.read_file('25.광양시_도시계획(공공문화체육시설).geojson')

parkingLot_raw = pd.read_csv('광양시_주차장_공간정보_전처리.csv')
campsite_raw = pd.read_csv('광양시_대중집합시설_야영장_전처리.csv')
traf_parkingLot_raw = pd.read_csv("광양시_도시계획(교통시설)_전처리.csv")
building_raw = pd.read_csv('광양시_건물정보_전처리.csv') 

In [ ]:
#CulPys_raw와 chargingStation_raw에 category컬럼 추가
CulPys_raw['category'] = '공공문화체육시설'
chargingStation_raw['category'] = '충전기'

In [ ]:
#충전기를 제외한 카테고리에서 추가할 컬럼인 '완속충전기_설치가능수량'을 충전소데이터에 미리 추가
#완속충전기일 경우 1, 급속충전기일 경우 0을 넣음

chargingStation_raw['완속충전기_설치가능여부'] = np.nan
for i in range(len(chargingStation_raw)):
    if chargingStation_raw['급속/완속'][i] == '완속':
        chargingStation_raw['완속충전기_설치가능여부'][i] = 1
    else:
        chargingStation_raw['완속충전기_설치가능여부'][i] = 0
chargingStation_raw

In [ ]:
#전처리된 모든 테이블을 합침
raw_table = pd.concat([parkingLot_raw, traf_parkingLot_raw, campsite_raw, CulPys_raw, chargingStation_raw, building_raw], ignore_index=True)

환경부 2020년 전기자동차 보급 및 충전인프라 구축사업 충전인프라 설치운영지침에 따르면   
해당 장소에 기 설치된 충전기가 없는 경우
#### 해당 장소의 주차단위구획 수× (0.01 + 해당 시‧도의 최근 3년간 신규 차량등록대수 분의 신규 전기차 등록대수) 까지 설치가 가능하다

전라남도청이 공개한 2019년 말 기준 광양시의 지난 3년간의 자동차 등록 현황 대수는    
87,990대(2019년 말) - 78,235대(2016년 9월 기준) = 9755대이다.

In [ ]:
#각 행정구역 연도별 등록된 자동차의 수
ElecCar_raw = pd.read_csv('06.광양시_전기차보급현황(연도별,읍면동별).csv')
adm = ElecCar_raw.행정구역.unique()

x = []
y = []
z = []
q = []
for i in range(len(ElecCar_raw)):
    if ElecCar_raw.기준년도[i] == 2017:
        x.append(ElecCar_raw.보급현황[i])
    elif ElecCar_raw.기준년도[i] == 2018:
        y.append(ElecCar_raw.보급현황[i])
    elif ElecCar_raw.기준년도[i] == 2019:
        z.append(ElecCar_raw.보급현황[i])
    else:
        q.append(ElecCar_raw.보급현황[i])


data = {'administration': adm, '2017' : x, '2018' : y , "2019" : z, '2020': q}
ElecCar = pd.DataFrame(data)
ElecCar['2017'].astype('int')
ElecCar['2018'].astype('int')
ElecCar['2019'].astype('int')
ElecCar['2020'].astype('int')
ElecCar      

administration  2017  2018  2019  2020
0             광양읍    17     1    44    40
1             봉강면     0     0     4     0
2             옥룡면     3     0     3     5
3             옥곡면     3     0     2     3
4             진상면     1     0     2     2
5             진월면     1     0     2     2
6             다압면     0     0     0     0
7             골약동     2     1     1     0
8             중마동    17     8    27    26
9             광영동     3     0     6     3
10            태인동     1     0     0     0
11            금호동     5     0     9     9

In [ ]:
#각 행정구역별 3년간 신규 전기차 등록대수
elist = []
for i in range(len(ElecCar)):
    a = 0
    for j in range(1, len(ElecCar.columns)-1):
        if ElecCar.loc[i][j] < ElecCar.loc[i][j+1]:
            x = ElecCar.loc[i][j+1] - ElecCar.loc[i][j]
            a += x
    elist.append(a)

administrative = gyboundary.ADM_DR_NM.tolist()
administrative.remove('광양읍')
administrative.insert(0, '광양읍')
data = {'administration': administrative, 'supply' : elist}
ElecCar_Supply = pd.DataFrame(data)
total = sum(ElecCar_Supply.supply)
ElecCar_Supply

administration  supply
0             광양읍      43
1             봉강면       4
2             옥룡면       5
3             옥곡면       3
4             진상면       2
5             진월면       2
6             다압면       0
7             골약동       0
8             중마동      19
9             광영동       6
10            태인동       0
11            금호동       9

In [ ]:
#광양시 3년간 신규 전기차 등록대수
total_new_eleccar = ElecCar_Supply['supply'].sum()
total_new_eleccar

### 2.2.2 인구분포 & 자동차 등록현황

In [ ]:
population = gpd.read_file("08.광양시_격자별인구현황(100X100).geojson")
car = gpd.read_file("03.광양시_자동차등록현황_격자(100X100).geojson")

In [ ]:
population.loc[population['val'].apply(pd.isna), 'val'] = 0    #NaN값 0으로 치환
population=population[population['val']!=0]                    #인구수가 0인 곳 제외
population_lon_lat = np.stack([population['geometry'].centroid.x, population['geometry'].centroid.y], axis=1).reshape([1, -1, 2])

car = car[car['totale']!=0]             #자동차수가 0인 곳 제외
car_lon_lat = np.stack([car['geometry'].centroid.x, car['geometry'].centroid.y], axis=1).reshape([1, -1, 2])
#차 속도 = 60km/h & 15분 거리 이내의 충전소에 간다고 가정 --> 15분에 15km (15000m)
speed = 60
distance = 60*1000/4

scale = sum([
    *(population['geometry'].bounds['maxx'] - population['geometry'].bounds['minx']),
    *(population['geometry'].bounds['maxy'] - population['geometry'].bounds['miny']),
]) / (2 * len(population)) / 100

### 2.2.3 학습테이블을 리턴하는 함수 생성 

In [ ]:
def make_table(table):
    table.drop(['주차장명칭', '구분', '유료/무료', '주소', 'PRESENT_SN', 'DGM_NM', 'DGM_LT','명칭','충전소명', '충전소위치', '충전기 운영기관', '충전기용량', '이용대수', '충전기타입','요금정보(원/kw)'], axis=1, inplace=True)
    
    for i in range(len(table)):
        if math.isnan(table['lon'][i]):
            table['lon'][i] = table['geometry'][i].centroid.x
            table['lat'][i] = table['geometry'][i].centroid.y
    table['geometry'] = table.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)
    
    table.rename(columns={"DGM_AR":"area"}, inplace=True)         
        
    #계산한 값의 의미는 설치 가능한 완속충전기의 수량이므로 그 값이 1이상이면 설치 가능하다고 생각하여 1로, 1미만이면 0으로 계산.    
    for i in range(len(table)):
        if math.isnan(table['완속충전기_설치가능여부'][i]):
            if table['주차면수'][i] * (0.01 + total_new_eleccar/9755) >= 1:
                table['완속충전기_설치가능여부'][i] = 1
            else:
                table['완속충전기_설치가능여부'][i] = 0
    
    
    lon_lat = np.stack([table.lon,table.lat], axis=1).reshape([-1,1,2])
    
    #인구분포계산
    인구분포_list = []
    population_condition = np.sum((lon_lat - population_lon_lat)**2, axis=2)**0.5 < distance*scale
    인구분포_list = np.array([population.loc[x,'val'].mean() for x in population_condition])
    table['인구분포'] = 인구분포_list    
    
    #등록되어있는 자동차분포 계산
    자동차분포_list = []
    car_condition = np.sum((lon_lat - car_lon_lat)**2, axis=2)**0.5 < distance*scale
    자동차분포_list = np.array([car.loc[x,'totale'].mean() for x in car_condition])
    table['자동차등록현황'] = 자동차분포_list
       
    #소유주체구분 --> 0 : 개인, 1 : 개인아님, 2 : None&법인
    table['소유주체'] = table['소유주체'].fillna(2)
    table['소유주체'] = table['소유주체'].replace({"민간":0,"개인":0, "종종":0, "종교단체":0,"공공":1, "군유지":1,"국유지":1,"시":1,"도유지":1,"법인":2})
    table['소유주체'] = table['소유주체'].astype(int)
    
    table['administration']=np.nan
    for i in range((len(table))):
        for j in range(len(gyboundary)):
            if table.geometry[i].within(gyboundary.geometry[j]) ==True:
                table['administration'][i] = gyboundary.ADM_DR_NM[j]
                
    table['전기차증가량'] = np.nan
    for i in range(len(table)):
        for j in range(len(ElecCar_Supply)):
            if table['administration'][i] == ElecCar_Supply['administration'][j]:
                table['전기차증가량'][i] = ElecCar_Supply['supply'][j]
    
    not_in_Gwangyang = table[table['administration'].isnull()]
    table.drop(table.index[not_in_Gwangyang.index.tolist()], inplace=True)
    
    
    table.reset_index(drop=True,inplace=True)
    return table


In [ ]:
table=make_table(raw_table)
table

### 2.2.4 표준화함수

In [ ]:
population_mean = table['인구분포'].mean()
population_std = table['인구분포'].std()
car_mean = table['자동차등록현황'].mean()
car_std = table['자동차등록현황'].std()
eleccar_increment_mean = table['전기차증가량'].mean()
eleccar_increment_std = table['전기차증가량'].std()

def preprocess(df):
    df = df.copy()
    df['인구분포'] = (df['인구분포'] - population_mean) / (population_std + 1e-3)
    df['자동차등록현황'] = (df['자동차등록현황'] - car_mean) / (car_std + 1e-3)    
    df['전기차증가량'] = (df['전기차증가량'] - eleccar_increment_mean) / (eleccar_increment_std + 1e-3)    
    return df

In [ ]:
table = preprocess(table)
table

In [ ]:
#table을 geojson파일 형태로 추출
table_gpd = GeoDataFrame(table, crs="EPSG:4326", geometry=[shapely.geometry.Point(xy) for xy in zip(table.lon, table.lat)])
table_gpd.to_file("table.geojson", driver='GeoJSON')

## 2.3 매핑

### 2.3.1 ElecCar_Supply를 활용하여 각 행정구역별 3년간 증가한 전기차 수 매핑

In [ ]:
ElecCar_Supply.set_index('administration')

mm1 = folium.Map(location=center, zoom_start=11)
mm1.choropleth(geo_data=gyboundary, data=ElecCar_Supply,
             columns=[ElecCar_Supply.index, 'supply'], fill_color='PuRd',
             key_on ='feature.properties.ADM_DR_NM', legend_name='new_Eleccar')
mm1

### 2.3.2 등록되어있는 자동차 heatmap으로 표현

In [ ]:
자동차 = gpd.read_file("03.광양시_자동차등록현황_격자(100X100).geojson")

자동차 = gpd.read_file("03.광양시_자동차등록현황_격자(100X100).geojson")
자동차_not_zero = 자동차[자동차['totale']!=0]     #totale이 0인 값을 제외하여 자동차_not_zero라는 데이터프레임으로 저장
자동차_not_zero.reset_index(drop=True, inplace=True)

# 자동차 격자의 geometry가 어느 행정구역에 속해있는지 파악 

자동차_not_zero['행정구역'] = np.nan
for i in range(len(자동차_not_zero)):
    for j in range(len(행정경계)):
        if 자동차_not_zero['geometry'][i].within(행정경계.geometry[j]) == True:
            자동차_not_zero['행정구역'][i] = 행정경계.ADM_DR_NM[j]
            
자동차_전처리 = 자동차_not_zero[자동차_not_zero['행정구역'].notnull()]   #행정구역에 속해있지 않는 경우 제외
자동차_전처리.reset_index(drop=True, inplace=True)
자동차_전처리

id  totale                                           geometry 행정구역
0       4179       1  POLYGON ((127.53449 35.07396, 127.53539 35.073...  봉강면
1      10366       1  POLYGON ((127.54796 34.96950, 127.54886 34.969...  광양읍
2      10767       2  POLYGON ((127.54886 34.97097, 127.54976 34.970...  광양읍
3      10768       2  POLYGON ((127.54886 34.97023, 127.54976 34.970...  광양읍
4      10769       2  POLYGON ((127.54886 34.96950, 127.54976 34.969...  광양읍
...      ...     ...                                                ...  ...
2579  114689       1  POLYGON ((127.78063 35.00924, 127.78152 35.009...  진월면
2580  115088       1  POLYGON ((127.78152 35.01218, 127.78242 35.012...  진월면
2581  115090       1  POLYGON ((127.78152 35.01071, 127.78242 35.010...  진월면
2582  115492       1  POLYGON ((127.78242 35.01144, 127.78332 35.011...  진월면
2583  116026       3  POLYGON ((127.78332 34.91500, 127.78422 34.915...  금호동

[2584 rows x 4 columns]

In [ ]:
#heatmap으로 표현하기 위해 자동차_전처리의 geometry컬럼을 이용하여 lon,lat컬럼을 구함
자동차_point = 자동차_전처리.copy()

자동차_point['lon'] = np.nan
자동차_point['lat'] = np.nan
for i in range(len(자동차_point)):
    자동차_point['lon'][i] = 자동차_point['geometry'][i].centroid.x
    자동차_point['lat'][i] = 자동차_point['geometry'][i].centroid.y
자동차_point['geometry'] = 자동차_point.apply(lambda row : Point([row['lon'], row['lat']]), axis=1)

자동차_point

id  totale                    geometry 행정구역         lon        lat
0       4179       1  POINT (127.53494 35.07359)  봉강면  127.534937  35.073591
1      10366       1  POINT (127.54841 34.96913)  광양읍  127.548412  34.969127
2      10767       2  POINT (127.54931 34.97060)  광양읍  127.549310  34.970599
3      10768       2  POINT (127.54931 34.96986)  광양읍  127.549310  34.969863
4      10769       2  POINT (127.54931 34.96913)  광양읍  127.549310  34.969127
...      ...     ...                         ...  ...         ...        ...
2579  114689       1  POINT (127.78108 35.00887)  진월면  127.781075  35.008869
2580  115088       1  POINT (127.78197 35.01181)  진월면  127.781974  35.011812
2581  115090       1  POINT (127.78197 35.01034)  진월면  127.781974  35.010340
2582  115492       1  POINT (127.78287 35.01108)  진월면  127.782872  35.011076
2583  116026       3  POINT (127.78377 34.91463)  금호동  127.783770  34.914635

[2584 rows x 6 columns]

In [ ]:
center = (34.9408,127.696)
mm2 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(gyboundary).add_to(mm2)
HeatMap(zip(자동차_point['lat'],자동차_point['lon'],자동차_point['totale']), min_opacity=0.1,
                   max_val=5,
                   radius=10, blur=15,
                   max_zoom=5).add_to(mm2)
mm2

### 2.3.3 인구 수 매핑

In [ ]:
격자별인구 = gpd.read_file("08.광양시_격자별인구현황(100X100).geojson")

격자별인구.loc[격자별인구['val'].apply(pd.isna), 'val'] = 0
격자별인구 = 격자별인구[격자별인구['val'] != 0]
격자별인구.reset_index(drop=True, inplace=True)

격자별인구['lon'] = np.nan
격자별인구['lat'] = np.nan
for i in range(len(격자별인구)):
    격자별인구['lon'][i] = 격자별인구['geometry'][i].centroid.x
    격자별인구['lat'][i] = 격자별인구['geometry'][i].centroid.y
    
격자별인구

gid   val                                           geometry  \
0     라라044638  10.0  MULTIPOLYGON (((127.54820 34.96908, 127.54820 ...   
1     라라045637  11.0  MULTIPOLYGON (((127.54930 34.96818, 127.54930 ...   
2     라라045638  25.0  MULTIPOLYGON (((127.54930 34.96908, 127.54930 ...   
3     라라046633   6.0  MULTIPOLYGON (((127.55039 34.96457, 127.55039 ...   
4     라라046637  21.0  MULTIPOLYGON (((127.55039 34.96818, 127.55039 ...   
...        ...   ...                                                ...   
2030  라라256682  10.0  MULTIPOLYGON (((127.78057 35.00844, 127.78057 ...   
2031  라라256684  12.0  MULTIPOLYGON (((127.78058 35.01024, 127.78058 ...   
2032  라라256686  10.0  MULTIPOLYGON (((127.78058 35.01205, 127.78059 ...   
2033  라라257684  16.0  MULTIPOLYGON (((127.78167 35.01024, 127.78168 ...   
2034  라라257685   9.0  MULTIPOLYGON (((127.78168 35.01114, 127.78168 ...   

             lon        lat  
0     127.548748  34.969529  
1     127.549843  34.968627  
2     127.549844  34.969528  
3     127.550936  34.965019  
4     127.550939  34.968626  
...          ...        ...  
2030  127.781121  35.008890  
2031  127.781127  35.010693  
2032  127.781133  35.012497  
2033  127.782223  35.010691  
2034  127.782226  35.011593  

[2035 rows x 5 columns]

In [ ]:
mm3 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(gyboundary).add_to(mm3)
HeatMap(zip(격자별인구['lat'],격자별인구['lon'], 격자별인구['val']), min_opacity=0.1,
                   max_val=5,
                   radius=10, blur=15,
                   max_zoom=5).add_to(mm3)
mm3

## 2.4 군집화 & 최종 위치 선정

In [ ]:
충전기 = pd.read_csv("01.광양시_충전기설치현황.csv")
행정경계 = gpd.read_file('20.광양시_행정경계(읍면동).geojson')
개발행위제한구역 = gpd.read_file("23.광양시_개발행위제한구역.geojson")
환경기초시설= gpd.read_file('28.광양시_도시계획(환경기초시설).geojson')
table = gpd.read_file('table.geojson')

### 2.4.1 전처리한 테이블을 급속 / 완속으로 나눔

In [ ]:
#카테고리에서 충전기를 제외
충전기제외 = table[table['category']!='충전기']
충전기제외.reset_index(drop=True, inplace=True)
충전기제외

area   주차면수         lon        lat category 소유주체 급속/완속  완속충전기_설치가능여부  \
0     4189.00  161.0  127.586883  34.970324      주차장    1  None           1.0   
1     2968.00  125.0  127.695428  34.936252      주차장    1  None           1.0   
2     2836.00   89.0  127.584586  34.975637      주차장    1  None           1.0   
3     1980.00   52.0  127.580683  34.970130      주차장    1  None           1.0   
4     1970.00   64.0  127.580707  34.972523      주차장    1  None           1.0   
...       ...    ...         ...        ...      ...  ...   ...           ...   
1161    79.95    0.0  127.768449  34.985126      휴게소    2  None           0.0   
1162    48.00    0.0  127.768300  34.984707      휴게소    2  None           0.0   
1163    77.49    0.0  127.769068  34.985767      휴게소    2  None           0.0   
1164    54.00    0.0  127.769183  34.985841      휴게소    1  None           0.0   
1165  2195.59    8.0  127.769283  34.985714      휴게소    2  None           0.0   

          인구분포   자동차등록현황 administration    전기차증가량                    geometry  
0     0.652892  0.607904            광양읍  1.262407  POINT (127.58688 34.97032)  
1    -0.278347 -0.157118            중마동 -0.162234  POINT (127.69543 34.93625)  
2     0.597602  0.481367            광양읍  1.262407  POINT (127.58459 34.97564)  
3     0.803955  0.568861            광양읍  1.262407  POINT (127.58068 34.97013)  
4     0.774028  0.561439            광양읍  1.262407  POINT (127.58071 34.97252)  
...        ...       ...            ...       ...                         ...  
1161  0.538225  1.059607            진월면 -1.171355  POINT (127.76845 34.98513)  
1162  0.538225  1.054870            진월면 -1.171355  POINT (127.76830 34.98471)  
1163  0.547037  1.059607            진월면 -1.171355  POINT (127.76907 34.98577)  
1164  0.547037  1.059607            진월면 -1.171355  POINT (127.76918 34.98584)  
1165  0.547037  1.073807            진월면 -1.171355  POINT (127.76928 34.98571)  

[1166 rows x 13 columns]

소유주체 --> 0 : 개인, 1 : 개인아님, 2 : None&법인  
소유주체의 2에 해당하는 None과 법인은 소유주체를 판단하기 어려워서 개인(0)과 함께 완속충전기만 설치하기로 함.

완속충전기 --> 소유주체 : 0,1,2 (소유주체 구분없이 모두)  
급속충전기 --> 소유주체 : 1

또한 완속충전기는 '완속충전기_설치가능여부'컬럼 중 값이 1인 것들만 추출함

### 1) 완속충전기

In [ ]:
완속충전기= 충전기제외[충전기제외['완속충전기_설치가능여부']==1]
완속충전기.reset_index(drop=True, inplace=True)
완속충전기

area   주차면수         lon        lat category 소유주체 급속/완속  \
0     4189.000  161.0  127.586883  34.970324      주차장    1  None   
1     2968.000  125.0  127.695428  34.936252      주차장    1  None   
2     2836.000   89.0  127.584586  34.975637      주차장    1  None   
3     1980.000   52.0  127.580683  34.970130      주차장    1  None   
4     1970.000   64.0  127.580707  34.972523      주차장    1  None   
..         ...    ...         ...        ...      ...  ...   ...   
412    811.780  207.0  127.565805  34.969112       주거    2  None   
413    802.080  207.0  127.563863  34.969020       주거    2  None   
414    631.195   65.0  127.699912  34.990774       주거    2  None   
415    121.290   83.0  127.589988  34.975036       주거    0  None   
416  43124.350  626.0  127.566398  34.962620     쇼핑센터    2  None   

     완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0             1.0  0.652892  0.607904            광양읍  1.262407   
1             1.0 -0.278347 -0.157118            중마동 -0.162234   
2             1.0  0.597602  0.481367            광양읍  1.262407   
3             1.0  0.803955  0.568861            광양읍  1.262407   
4             1.0  0.774028  0.561439            광양읍  1.262407   
..            ...       ...       ...            ...       ...   
412           1.0  0.745944  0.496053            광양읍  1.262407   
413           1.0  0.699774  0.345523            광양읍  1.262407   
414           1.0 -0.576433 -0.413918            옥곡면 -1.111995   
415           1.0  0.549710  0.459291            광양읍  1.262407   
416           1.0  0.869954  0.519449            광양읍  1.262407   

                       geometry  
0    POINT (127.58688 34.97032)  
1    POINT (127.69543 34.93625)  
2    POINT (127.58459 34.97564)  
3    POINT (127.58068 34.97013)  
4    POINT (127.58071 34.97252)  
..                          ...  
412  POINT (127.56580 34.96911)  
413  POINT (127.56386 34.96902)  
414  POINT (127.69991 34.99077)  
415  POINT (127.58999 34.97504)  
416  POINT (127.56640 34.96262)  

[417 rows x 13 columns]

In [ ]:
개발행위제한구역

PRESENT_SN      DGM_NM   DGM_AR  DGM_LT  \
0  46230UQ171PS201202010010  개발행위허가제한지역   472951    2882   
1  46230UQ171PS201202010005  개발행위허가제한지역   285822    2693   
2  46230UQ171PS201202010012  개발행위허가제한지역   224847    3035   
3  46230UQ171PS201202010004  개발행위허가제한지역  1005133    6145   
4  46230UQ171PS201202010003  개발행위허가제한지역   428173    8369   
5  46230UQ171PS201202010002  개발행위허가제한지역  1751016    6324   
6  46230UQ171PS201202010011  개발행위허가제한지역   298061    3022   
7  46230UQ171PS201309010013  개발행위허가제한지역  2930431    6620   

                                            geometry  
0  MULTIPOLYGON (((127.75655 34.95331, 127.75639 ...  
1  MULTIPOLYGON (((127.68861 34.93046, 127.68741 ...  
2  MULTIPOLYGON (((127.66325 34.91089, 127.66325 ...  
3  MULTIPOLYGON (((127.62452 34.91111, 127.62508 ...  
4  MULTIPOLYGON (((127.66049 34.91279, 127.66047 ...  
5  MULTIPOLYGON (((127.57814 34.93243, 127.59923 ...  
6  MULTIPOLYGON (((127.67485 34.93474, 127.67484 ...  
7  MULTIPOLYGON (((127.63141 34.93677, 127.63141 ...

In [ ]:
#개발행위제한구역에 속해있는 곳은 제외

개발제한구역_완속 = []
for i in range(len(완속충전기.geometry)):
    for j in range(len(개발행위제한구역.geometry)):
        if 완속충전기.geometry[i].within(개발행위제한구역.geometry[j]) == True:
            개발제한구역_완속.append(i)
개발제한구역_완속            

[35, 95, 96, 112, 113, 114]

In [ ]:
완속충전기.drop(완속충전기.index[개발제한구역_완속], inplace=True)
완속충전기.reset_index(drop=True, inplace=True)
완속충전기

area   주차면수         lon        lat category 소유주체 급속/완속  \
0     4189.000  161.0  127.586883  34.970324      주차장    1  None   
1     2968.000  125.0  127.695428  34.936252      주차장    1  None   
2     2836.000   89.0  127.584586  34.975637      주차장    1  None   
3     1980.000   52.0  127.580683  34.970130      주차장    1  None   
4     1970.000   64.0  127.580707  34.972523      주차장    1  None   
..         ...    ...         ...        ...      ...  ...   ...   
406    811.780  207.0  127.565805  34.969112       주거    2  None   
407    802.080  207.0  127.563863  34.969020       주거    2  None   
408    631.195   65.0  127.699912  34.990774       주거    2  None   
409    121.290   83.0  127.589988  34.975036       주거    0  None   
410  43124.350  626.0  127.566398  34.962620     쇼핑센터    2  None   

     완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0             1.0  0.652892  0.607904            광양읍  1.262407   
1             1.0 -0.278347 -0.157118            중마동 -0.162234   
2             1.0  0.597602  0.481367            광양읍  1.262407   
3             1.0  0.803955  0.568861            광양읍  1.262407   
4             1.0  0.774028  0.561439            광양읍  1.262407   
..            ...       ...       ...            ...       ...   
406           1.0  0.745944  0.496053            광양읍  1.262407   
407           1.0  0.699774  0.345523            광양읍  1.262407   
408           1.0 -0.576433 -0.413918            옥곡면 -1.111995   
409           1.0  0.549710  0.459291            광양읍  1.262407   
410           1.0  0.869954  0.519449            광양읍  1.262407   

                       geometry  
0    POINT (127.58688 34.97032)  
1    POINT (127.69543 34.93625)  
2    POINT (127.58459 34.97564)  
3    POINT (127.58068 34.97013)  
4    POINT (127.58071 34.97252)  
..                          ...  
406  POINT (127.56580 34.96911)  
407  POINT (127.56386 34.96902)  
408  POINT (127.69991 34.99077)  
409  POINT (127.58999 34.97504)  
410  POINT (127.56640 34.96262)  

[411 rows x 13 columns]

In [ ]:
환경기초시설

PRESENT_SN      DGM_NM   DGM_AR  DGM_LT  \
0   46230UQ158PS201202010007    하수종말처리시설    14403     558   
1   46230UQ158PS201202010008    하수종말처리시설     3712     243   
2   46230UQ158PS201202010009    폐수종말처리시설    21429     581   
3   46230UQ158PS201202010010    폐수종말처리시설     9816     413   
4   46230UQ158PS201202010003      분뇨처리시설     4716     282   
5   46230UQ158PS201202010004  기타 폐기물처리시설  1253423    4747   
6   46230UQ158PS201202010005  기타 폐기물처리시설    56119     995   
7   46230UQ158PS201202010006    하수종말처리시설    62644    1028   
8   46230UQ158PS201202010011  기타 폐기물처리시설   165300    3498   
9   46230UQ158PS201308010002    하수종말처리시설    44842     869   
10  46230UQ158PS201309010001  기타 폐기물처리시설    27872     788   
11  46230UQ158PS201809110011    폐수종말처리시설    12000     474   
12  46230UQ158PS201309010012    폐수종말처리시설    12297     487   
13  46230UQ158PS201809110013  기타 폐기물처리시설    18099     548   
14  46230UQ158PS201809110014  기타 폐기물처리시설     6000     313   
15  46230UQ158PS201809110015    기타 하수도시설       44      29   

                                             geometry  
0   MULTIPOLYGON (((127.73116 34.95513, 127.73113 ...  
1   MULTIPOLYGON (((127.74574 34.96011, 127.74557 ...  
2   MULTIPOLYGON (((127.76086 34.93416, 127.76070 ...  
3   MULTIPOLYGON (((127.76746 34.94624, 127.76746 ...  
4   MULTIPOLYGON (((127.60798 34.93196, 127.60792 ...  
5   MULTIPOLYGON (((127.65460 34.95111, 127.65271 ...  
6   MULTIPOLYGON (((127.67543 34.96926, 127.67542 ...  
7   MULTIPOLYGON (((127.69227 34.92799, 127.68882 ...  
8   MULTIPOLYGON (((127.78418 34.91192, 127.78410 ...  
9   MULTIPOLYGON (((127.58642 34.92640, 127.58655 ...  
10  MULTIPOLYGON (((127.74338 34.96236, 127.74343 ...  
11  MULTIPOLYGON (((127.58942 34.92485, 127.58943 ...  
12  MULTIPOLYGON (((127.62102 34.90346, 127.62214 ...  
13  MULTIPOLYGON (((127.59031 34.92502, 127.59036 ...  
14  MULTIPOLYGON (((127.62493 34.90585, 127.62554 ...  
15  MULTIPOLYGON (((127.72368 34.96744, 127.72363 ...

In [ ]:
#환경기초시설에 속해있는 곳은 제외하려했으나 속해있는 곳이 없음
환경기초시설_완속 = []
for i in range(len(완속충전기.geometry)):
    for j in range(len(환경기초시설.geometry)):
        if 완속충전기.geometry[i].within(환경기초시설.geometry[j]) == True:
            환경기초시설_완속.append(i)
            
환경기초시설_완속

[]

### 2) 급속충전기

In [ ]:
급속충전기 = 충전기제외[충전기제외['소유주체']=='1']       #소유주체가 1인것만 추출
급속충전기['소유주체'] = 급속충전기['소유주체'].astype(int)
급속충전기.reset_index(drop=True, inplace=True)
급속충전기

area   주차면수         lon        lat   category  소유주체 급속/완속  \
0    4189.00  161.0  127.586883  34.970324        주차장     1  None   
1    2968.00  125.0  127.695428  34.936252        주차장     1  None   
2    2836.00   89.0  127.584586  34.975637        주차장     1  None   
3    1980.00   52.0  127.580683  34.970130        주차장     1  None   
4    1970.00   64.0  127.580707  34.972523        주차장     1  None   
..       ...    ...         ...        ...        ...   ...   ...   
291  2384.17   14.0  127.575568  34.984567  기타문화및집회시설     1  None   
292   290.25    3.0  127.586498  34.987780  기타문화및집회시설     1  None   
293   888.04    7.0  127.582551  34.973514        도서관     1  None   
294   471.58    4.0  127.607315  34.974085        도서관     1  None   
295    54.00    0.0  127.769183  34.985841        휴게소     1  None   

     완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0             1.0  0.652892  0.607904            광양읍  1.262407   
1             1.0 -0.278347 -0.157118            중마동 -0.162234   
2             1.0  0.597602  0.481367            광양읍  1.262407   
3             1.0  0.803955  0.568861            광양읍  1.262407   
4             1.0  0.774028  0.561439            광양읍  1.262407   
..            ...       ...       ...            ...       ...   
291           0.0  0.554751  0.045876            광양읍  1.262407   
292           0.0  0.478617  0.298718            광양읍  1.262407   
293           0.0  0.708795  0.569017            광양읍  1.262407   
294           0.0  0.075735  0.145442            광양읍  1.262407   
295           0.0  0.547037  1.059607            진월면 -1.171355   

                       geometry  
0    POINT (127.58688 34.97032)  
1    POINT (127.69543 34.93625)  
2    POINT (127.58459 34.97564)  
3    POINT (127.58068 34.97013)  
4    POINT (127.58071 34.97252)  
..                          ...  
291  POINT (127.57557 34.98457)  
292  POINT (127.58650 34.98778)  
293  POINT (127.58255 34.97351)  
294  POINT (127.60732 34.97408)  
295  POINT (127.76918 34.98584)  

[296 rows x 13 columns]

In [ ]:
#개발행위제한구역에 속해있는 곳은 제외

개발제한구역_급속 = []
for i in range(len(급속충전기.geometry)):
    for j in range(len(개발행위제한구역.geometry)):
        if 급속충전기.geometry[i].within(개발행위제한구역.geometry[j]) == True:
            개발제한구역_급속.append(i)
개발제한구역_급속    

[87, 144, 236, 237, 258]

In [ ]:
급속충전기.drop(급속충전기.index[개발제한구역_급속], inplace=True)
급속충전기.reset_index(drop=True, inplace=True)
급속충전기

area   주차면수         lon        lat   category  소유주체 급속/완속  \
0    4189.00  161.0  127.586883  34.970324        주차장     1  None   
1    2968.00  125.0  127.695428  34.936252        주차장     1  None   
2    2836.00   89.0  127.584586  34.975637        주차장     1  None   
3    1980.00   52.0  127.580683  34.970130        주차장     1  None   
4    1970.00   64.0  127.580707  34.972523        주차장     1  None   
..       ...    ...         ...        ...        ...   ...   ...   
286  2384.17   14.0  127.575568  34.984567  기타문화및집회시설     1  None   
287   290.25    3.0  127.586498  34.987780  기타문화및집회시설     1  None   
288   888.04    7.0  127.582551  34.973514        도서관     1  None   
289   471.58    4.0  127.607315  34.974085        도서관     1  None   
290    54.00    0.0  127.769183  34.985841        휴게소     1  None   

     완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0             1.0  0.652892  0.607904            광양읍  1.262407   
1             1.0 -0.278347 -0.157118            중마동 -0.162234   
2             1.0  0.597602  0.481367            광양읍  1.262407   
3             1.0  0.803955  0.568861            광양읍  1.262407   
4             1.0  0.774028  0.561439            광양읍  1.262407   
..            ...       ...       ...            ...       ...   
286           0.0  0.554751  0.045876            광양읍  1.262407   
287           0.0  0.478617  0.298718            광양읍  1.262407   
288           0.0  0.708795  0.569017            광양읍  1.262407   
289           0.0  0.075735  0.145442            광양읍  1.262407   
290           0.0  0.547037  1.059607            진월면 -1.171355   

                       geometry  
0    POINT (127.58688 34.97032)  
1    POINT (127.69543 34.93625)  
2    POINT (127.58459 34.97564)  
3    POINT (127.58068 34.97013)  
4    POINT (127.58071 34.97252)  
..                          ...  
286  POINT (127.57557 34.98457)  
287  POINT (127.58650 34.98778)  
288  POINT (127.58255 34.97351)  
289  POINT (127.60732 34.97408)  
290  POINT (127.76918 34.98584)  

[291 rows x 13 columns]

In [ ]:
#환경기초시설에 속해있는 곳은 제외하려했으나 속해있는 곳이 없음
환경기초시설_급속 = []
for i in range(len(급속충전기.geometry)):
    for j in range(len(환경기초시설.geometry)):
        if 급속충전기.geometry[i].within(환경기초시설.geometry[j]) == True:
            환경기초시설_급속.append(i)
            
환경기초시설_급속

[]

In [ ]:
#광양시청 경위도 : 34.9408, 127.696  
#folium에 mapping할 때 center경위도를 광양시청의 경위도로 한다.
center = (34.9408,127.696)



m1 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(행정경계).add_to(m1)

for i in range(len(완속충전기)):
    sub_lat = 완속충전기.loc[i,"lat"]
    sub_lon = 완속충전기.loc[i,'lon']
    title = 완속충전기.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='red', radius=5, tooltip=title).add_to(m1)
    
for i in range(len(급속충전기)):
    sub_lat = 급속충전기.loc[i,"lat"]
    sub_lon = 급속충전기.loc[i,'lon']
    title = 완속충전기.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='blue', radius=5, tooltip=title).add_to(m1)
        
m1

### 2.4.2 K-means clustering 이용하여 충전기 설치 할 위치들 군집화 후 위치선정

### 1) 급속충전기

인덱스끼리 '인구분포', '자동차등록현황','전기차증가량'컬럼값을 비교하여 세 값 중 두 개의 값이 큰 인덱스의 count값을 1씩 증가하여 최종적으로 sort_list에 그 값을 담음

In [ ]:
급속충전기_정렬 = 급속충전기[['인구분포','자동차등록현황','전기차증가량']]
human=list(급속충전기_정렬['인구분포'])
car=list(급속충전기_정렬['자동차등록현황'])
eleccar=list(급속충전기_정렬['전기차증가량'])

sort_list=[]
for i in range(len(human)):
    sort_list.append(0)

def weight_count(idx1, idx2):
    _num1 = 0
    _num2 = 0
    _listnm=[human, car, eleccar]
    for _list in _listnm:
        if _list[_sort] > _list[_sort2]:
            _num1+=1
        elif _list[_sort] == _list[_sort2]:
            pass
        else:
            _num2+=1
    return _num1, _num2

_num=0
for _sort in range(0, len(human)):
    for _sort2 in range(_sort+1, len(human)):
        _num1, _num2 = weight_count(_sort,_sort2)
        if _num1> _num2:
            sort_list[_num]+=1
        elif _num1 == _num2:
            pass
        else:
            if _num<=294:
                sort_list[_sort2]+=1
    _num+=1

print(sort_list)

[233, 118, 210, 245, 242, 206, 202, 170, 182, 191, 180, 221, 202, 174, 166, 250, 177, 231, 180, 173, 177, 182, 220, 215, 199, 176, 177, 197, 148, 144, 156, 226, 233, 237, 193, 164, 167, 163, 170, 170, 186, 186, 176, 283, 180, 286, 175, 255, 189, 190, 185, 93, 69, 107, 57, 125, 131, 136, 111, 121, 107, 115, 72, 64, 140, 57, 105, 127, 123, 118, 57, 103, 128, 127, 66, 96, 128, 52, 54, 117, 112, 75, 71, 100, 78, 104, 72, 160, 157, 83, 74, 105, 68, 62, 77, 83, 86, 113, 77, 69, 81, 81, 83, 63, 198, 279, 266, 261, 248, 288, 262, 257, 41, 33, 36, 35, 39, 37, 38, 47, 43, 45, 27, 20, 32, 29, 157, 155, 214, 273, 274, 278, 11, 14, 17, 169, 185, 182, 180, 172, 96, 100, 55, 17, 11, 14, 8, 26, 10, 7, 6, 25, 21, 24, 186, 182, 39, 102, 163, 191, 56, 131, 221, 220, 202, 180, 172, 198, 155, 133, 263, 262, 169, 87, 52, 185, 19, 16, 11, 128, 133, 131, 85, 93, 177, 289, 136, 65, 61, 22, 144, 156, 182, 242, 31, 30, 125, 115, 118, 93, 57, 69, 72, 86, 215, 206, 171, 262, 123, 42, 170, 163, 47, 43, 214, 276, 14

In [ ]:
급속충전기['인구분포_자동차등록_전기차']=sort_list
급속충전기

area   주차면수         lon        lat   category  소유주체 급속/완속  \
0    4189.00  161.0  127.586883  34.970324        주차장     1  None   
1    2968.00  125.0  127.695428  34.936252        주차장     1  None   
2    2836.00   89.0  127.584586  34.975637        주차장     1  None   
3    1980.00   52.0  127.580683  34.970130        주차장     1  None   
4    1970.00   64.0  127.580707  34.972523        주차장     1  None   
..       ...    ...         ...        ...        ...   ...   ...   
286  2384.17   14.0  127.575568  34.984567  기타문화및집회시설     1  None   
287   290.25    3.0  127.586498  34.987780  기타문화및집회시설     1  None   
288   888.04    7.0  127.582551  34.973514        도서관     1  None   
289   471.58    4.0  127.607315  34.974085        도서관     1  None   
290    54.00    0.0  127.769183  34.985841        휴게소     1  None   

     완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0             1.0  0.652892  0.607904            광양읍  1.262407   
1             1.0 -0.278347 -0.157118            중마동 -0.162234   
2             1.0  0.597602  0.481367            광양읍  1.262407   
3             1.0  0.803955  0.568861            광양읍  1.262407   
4             1.0  0.774028  0.561439            광양읍  1.262407   
..            ...       ...       ...            ...       ...   
286           0.0  0.554751  0.045876            광양읍  1.262407   
287           0.0  0.478617  0.298718            광양읍  1.262407   
288           0.0  0.708795  0.569017            광양읍  1.262407   
289           0.0  0.075735  0.145442            광양읍  1.262407   
290           0.0  0.547037  1.059607            진월면 -1.171355   

                       geometry  인구분포_자동차등록_전기차  
0    POINT (127.58688 34.97032)             233  
1    POINT (127.69543 34.93625)             118  
2    POINT (127.58459 34.97564)             210  
3    POINT (127.58068 34.97013)             245  
4    POINT (127.58071 34.97252)             242  
..                          ...             ...  
286  POINT (127.57557 34.98457)             158  
287  POINT (127.58650 34.98778)             164  
288  POINT (127.58255 34.97351)             233  
289  POINT (127.60732 34.97408)             155  
290  POINT (127.76918 34.98584)             195  

[291 rows x 14 columns]

#### kmeans군집화에 '인구분포','자동차등록현황','전기차증가량' 세 개의 컬럼을 넣고 20개의 군집으로 나타내기 위해 n_clusters를 20으로 설정

In [ ]:
x_급속 = 급속충전기[['인구분포','자동차등록현황','전기차증가량']]

kmeans_급속 = KMeans(n_clusters = 20, init='k-means++', max_iter=300, random_state=0)
kmeans_급속.fit(x_급속)

predict_급속 = pd.DataFrame(kmeans_급속.predict(x_급속))
predict_급속.columns=['군집']


#각 군집에 해당하는 인덱스를 '급속_index' 리스트에 넣음
급속_index=[[] for _ in range(20)]
for i in range(len(급속충전기)):
    _tmp2=predict_급속.iloc[i][0]
    급속_index[_tmp2].append(i)
    
    
급속_list = []

for i in range(20):
    df = 급속충전기.iloc[급속_index[i]]  #각 군집의 인덱스에 해당하는 데이터프레임 생성
    max_df = df[df.인구분포_자동차등록_전기차==max(df.인구분포_자동차등록_전기차)]     #각 군집에서 '인구분포_자동차등록_전기차'값이 가장 큰 행 추출
    max_df['군집'] = i
    급속_list.append(max_df)
    
급속_new_df = pd.concat(급속_list)
급속_new_df['급속/완속'] = '급속'
급속_new_df.reset_index(drop=True, inplace=True)
급속_new_df

area   주차면수         lon        lat category  소유주체 급속/완속  완속충전기_설치가능여부  \
0   1448.00   55.0  127.700268  34.939376      주차장     1    급속           1.0   
1   1449.00   48.0  127.700269  34.939377      주차장     1    급속           0.0   
2   4702.00  135.0  127.599294  35.101532      주차장     1    급속           1.0   
3    409.00   27.0  127.583395  34.973645      주차장     1    급속           0.0   
4   4300.00   65.0  127.758582  34.979305      주차장     1    급속           1.0   
5    161.00    7.0  127.756710  34.966051      주차장     1    급속           0.0   
6     14.06    0.0  127.683919  35.136115     공공시설     1    급속           0.0   
7    762.00   15.0  127.721717  34.960730      주차장     1    급속           0.0   
8    827.00   30.0  127.676139  35.090000      주차장     1    급속           0.0   
9    615.00   22.0  127.640598  34.911785      주차장     1    급속           0.0   
10  1251.00   52.0  127.607064  34.974006      주차장     1    급속           1.0   
11  1251.00   42.0  127.607064  34.974007      주차장     1    급속           0.0   
12   712.00   22.0  127.755977  34.943044      주차장     1    급속           0.0   
13   688.00   20.0  127.715877  34.974770      주차장     1    급속           0.0   
14  1715.00   57.0  127.719648  34.974372      주차장     1    급속           1.0   
15   185.00    4.0  127.576992  34.943998      주차장     1    급속           0.0   
16   720.00   30.0  127.617527  35.068381      주차장     1    급속           0.0   
17  4200.00   50.0  127.760591  34.976362      주차장     1    급속           0.0   
18   713.00   22.0  127.760665  34.977087      주차장     1    급속           0.0   
19  1313.00   44.0  127.698495  34.926713      주차장     1    급속           0.0   
20  2692.00    NaN  127.606442  34.942612      주차장     1    급속           0.0   
21  2692.00   87.0  127.606442  34.942614      주차장     1    급속           1.0   
22  1970.00   49.0  127.576642  34.974387      주차장     1    급속           0.0   
23  1970.00   66.0  127.576642  34.974388      주차장     1    급속           1.0   
24    36.00    0.0  127.762758  34.902292     공공시설     1    급속           0.0   
25  3486.00   94.0  127.564633  35.079183      주차장     1    급속           1.0   
26   622.00   22.0  127.678230  34.933951      주차장     1    급속           0.0   

        인구분포   자동차등록현황 administration    전기차증가량                    geometry  \
0  -0.243195 -0.125650            중마동 -0.162234  POINT (127.70027 34.93938)   
1  -0.243195 -0.125650            중마동 -0.162234  POINT (127.70027 34.93938)   
2  -3.792886 -4.151921            옥룡면 -0.993275  POINT (127.59929 35.10153)   
3   0.672852  0.529881            광양읍  1.262407  POINT (127.58339 34.97365)   
4   0.968742  1.305718            진월면 -1.171355  POINT (127.75858 34.97930)   
5   1.011955  1.283353            진월면 -1.171355  POINT (127.75671 34.96605)   
6  -8.730682 -8.726161            다압면 -1.290075  POINT (127.68392 35.13611)   
7  -0.184147 -0.167819            광영동 -0.933915  POINT (127.72172 34.96073)   
8  -2.801907 -2.881553            진상면 -1.171355  POINT (127.67614 35.09000)   
9   0.352775  0.462582            골약동 -1.290075  POINT (127.64060 34.91179)   
10  0.080942  0.161326            광양읍  1.262407  POINT (127.60706 34.97401)   
11  0.080942  0.161326            광양읍  1.262407  POINT (127.60706 34.97401)   
12  1.380898  1.681638            태인동 -1.290075  POINT (127.75598 34.94304)   
13 -0.436233 -0.317800            옥곡면 -1.111995  POINT (127.71588 34.97477)   
14 -0.433675 -0.343279            옥곡면 -1.111995  POINT (127.71965 34.97437)   
15  1.172016  0.844572            광양읍  1.262407  POINT (127.57699 34.94400)   
16 -2.057373 -2.160953            옥룡면 -0.993275  POINT (127.61753 35.06838)   
17  0.588708  0.892282            진월면 -1.171355  POINT (127.76059 34.97636)   
18  0.588708  0.892282            진월면 -1.171355  POINT (127.76066 34.97709)   
19 -0.026080  0.103988            중마동 -0.162234  POINT (127.69850 34.92671)   
20  0.303014  0.434911            광양읍  1.262407  POINT (127.60644 34.94261)   
21  0.303014  0.434911      

In [ ]:
# 인덱스 0과1, 10과11, 20과21, 22와23는 여러 주차장 데이터를 합치면서 생긴 중복된 데이터임. 둘 중 하나를 제거해줌

급속_new_df.drop([급속_new_df.index[0],급속_new_df.index[10],급속_new_df.index[20],급속_new_df.index[22]], inplace=True)
급속_new_df.reset_index(drop=True, inplace=True)
급속_new_df

area   주차면수         lon        lat category  소유주체 급속/완속  완속충전기_설치가능여부  \
0   1449.00   48.0  127.700269  34.939377      주차장     1    급속           0.0   
1   4702.00  135.0  127.599294  35.101532      주차장     1    급속           1.0   
2    409.00   27.0  127.583395  34.973645      주차장     1    급속           0.0   
3   4300.00   65.0  127.758582  34.979305      주차장     1    급속           1.0   
4    161.00    7.0  127.756710  34.966051      주차장     1    급속           0.0   
5     14.06    0.0  127.683919  35.136115     공공시설     1    급속           0.0   
6    762.00   15.0  127.721717  34.960730      주차장     1    급속           0.0   
7    827.00   30.0  127.676139  35.090000      주차장     1    급속           0.0   
8    615.00   22.0  127.640598  34.911785      주차장     1    급속           0.0   
9   1251.00   42.0  127.607064  34.974007      주차장     1    급속           0.0   
10   712.00   22.0  127.755977  34.943044      주차장     1    급속           0.0   
11   688.00   20.0  127.715877  34.974770      주차장     1    급속           0.0   
12  1715.00   57.0  127.719648  34.974372      주차장     1    급속           1.0   
13   185.00    4.0  127.576992  34.943998      주차장     1    급속           0.0   
14   720.00   30.0  127.617527  35.068381      주차장     1    급속           0.0   
15  4200.00   50.0  127.760591  34.976362      주차장     1    급속           0.0   
16   713.00   22.0  127.760665  34.977087      주차장     1    급속           0.0   
17  1313.00   44.0  127.698495  34.926713      주차장     1    급속           0.0   
18  2692.00   87.0  127.606442  34.942614      주차장     1    급속           1.0   
19  1970.00   66.0  127.576642  34.974388      주차장     1    급속           1.0   
20    36.00    0.0  127.762758  34.902292     공공시설     1    급속           0.0   
21  3486.00   94.0  127.564633  35.079183      주차장     1    급속           1.0   
22   622.00   22.0  127.678230  34.933951      주차장     1    급속           0.0   

        인구분포   자동차등록현황 administration    전기차증가량                    geometry  \
0  -0.243195 -0.125650            중마동 -0.162234  POINT (127.70027 34.93938)   
1  -3.792886 -4.151921            옥룡면 -0.993275  POINT (127.59929 35.10153)   
2   0.672852  0.529881            광양읍  1.262407  POINT (127.58339 34.97365)   
3   0.968742  1.305718            진월면 -1.171355  POINT (127.75858 34.97930)   
4   1.011955  1.283353            진월면 -1.171355  POINT (127.75671 34.96605)   
5  -8.730682 -8.726161            다압면 -1.290075  POINT (127.68392 35.13611)   
6  -0.184147 -0.167819            광영동 -0.933915  POINT (127.72172 34.96073)   
7  -2.801907 -2.881553            진상면 -1.171355  POINT (127.67614 35.09000)   
8   0.352775  0.462582            골약동 -1.290075  POINT (127.64060 34.91179)   
9   0.080942  0.161326            광양읍  1.262407  POINT (127.60706 34.97401)   
10  1.380898  1.681638            태인동 -1.290075  POINT (127.75598 34.94304)   
11 -0.436233 -0.317800            옥곡면 -1.111995  POINT (127.71588 34.97477)   
12 -0.433675 -0.343279            옥곡면 -1.111995  POINT (127.71965 34.97437)   
13  1.172016  0.844572            광양읍  1.262407  POINT (127.57699 34.94400)   
14 -2.057373 -2.160953            옥룡면 -0.993275  POINT (127.61753 35.06838)   
15  0.588708  0.892282            진월면 -1.171355  POINT (127.76059 34.97636)   
16  0.588708  0.892282            진월면 -1.171355  POINT (127.76066 34.97709)   
17 -0.026080  0.103988            중마동 -0.162234  POINT (127.69850 34.92671)   
18  0.303014  0.434911            광양읍  1.262407  POINT (127.60644 34.94261)   
19  0.759417  0.388829            광양읍  1.262407  POINT (127.57664 34.97439)   
20  1.568052  2.171627            금호동 -0.755835  POINT (127.76276 34.90229)   
21 -3.541354 -3.917943            봉강면 -1.052635  POINT (127.56463 35.07918)   
22 -0.289915 -0.173104            골약동 -1.290075  POINT (127.67823 34.93395)   

    인구분포_자동차등록_전기차  군집  
0              125   0  
1               10   1  
2              226   2  
3              273   3  
4              273   3  
5                1   4  
6             

In [ ]:
#현재 설치되어있는 급속충전기를 지도에 매핑하기 위해 데이터 전처리

설치된_급속충전기 = 충전기[충전기['급속/완속']=='급속']
설치된_급속충전기.reset_index(drop=True, inplace=True)
설치된_급속충전기

충전소명                                  충전소위치        충전기 운영기관  \
0       LF스퀘어 광양점                  전남 광양시 광양읍 순광로 466 1층  환경부(한국자동차환경협회)   
1     광양만권경제자유구역청          전남 광양시 광양읍 인덕로 1100(광양시 제2청사)  환경부(한국자동차환경협회)   
2    광양읍사무소 앞 주차장                   전남 광양시 광양읍 칠성리 948-1  환경부(한국자동차환경협회)   
3        한국전력광양지사                          전남 광양시 중동로 20            한국전력   
4         광영 근린공원                       전남 광양시 광영동 산41-3            한국전력   
5       대신증권앞 주차장                       전남 광양시 중동 1358-1  환경부(한국자동차환경협회)   
6    섬진강휴게소(부산방향)                 전남 광양시 진월면 섬진강 매화로 141  환경부(한국자동차환경협회)   
7    섬진강휴게소(부산방향)                 전남 광양시 진월면 섬진강 매화로 141  환경부(한국자동차환경협회)   
8    섬진강휴게소(순천방향)                   전남 광양시 진월면 신답길 24-14  환경부(한국자동차환경협회)   
9    섬진강휴게소(순천방향)                   전남 광양시 진월면 신답길 24-14  환경부(한국자동차환경협회)   
10         인동숲주차장               전남 광양시 광양읍 인서리 238 좌측주차장  환경부(한국자동차환경협회)   
11         인동숲주차장               전남 광양시 광양읍 인서리 238 좌측주차장  환경부(한국자동차환경협회)   
12  중마버스터미널 공영주차장                          전남 광양시 공영로 91  환경부(한국자동차환경협회)   
13     중마상설시장 주차장                       전남 광양시 주동 1732-3  환경부(한국자동차환경협회)   
14       홈플러스 광양점                        전남 광양시 항만11로 70            한국전력   
15       마동근린체육공원                    전남 광양시 마동 주차장 입구 좌측            한국전력   
16     광양중마호반리젠시빌   전남 광양시 공영로 39 실내지하 101103동 사이 지하주차장             한국전력   
17       태영1차 아파트    전남 광양시 광장로 112-11 실외노출 101동 관리사무소 앞            한국전력   
18       태영2차 아파트       전남 광양시 광장로 120 실외노출 201동 관리사무소 앞            한국전력   
19     성호2-1차 아파트      전남 광양시 광장로 70 실내지하 202동 앞 지하1층 우측            한국전력   
20   송보파인빌 6차 아파트               전남 광양시 진등6길 51 정문 604동 앞            한국전력   
21   송보파인빌 7차 아파트     전남 광양시 광양읍 와룡길 33 705동 707동 사이 주차장            한국전력   
22      남해오네뜨 아파트  전남 광양시 광양읍 와룡길 43 실내지하 109동 지하주차장 c15            한국전력   

   급속/완속       충전기용량  이용대수            충전기타입  요금정보(원/kw)         lon        lat  
0     급속  200KW 동시충전     2             DC콤보      255.70  127.568300  34.963002  
1     급속        50KW     1  DC차데모/AC3상/DC콤보      255.70  127.583323  34.980334  
2     급속  200KW 동시충전     2             DC콤보      255.70  127.580523  34.972300  
3     급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.691011  34.940027  
4     급속         NaN     2  DC차데모/AC3상/DC콤보      191.73  127.718854  34.960699  
5     급속  200KW 동시충전     2             DC콤보      255.70  127.694421  34.942039  
6     급속        50KW     1  DC차데모/AC3상/DC콤보      255.70  127.770993  34.984890  
7     급속      100KW      1  DC차데모/AC3상/DC콤보      255.70  127.770993  34.984890  
8     급속       100KW     1  DC차데모/AC3상/DC콤보      255.70  127.768300  34.984695  
9     급속        50KW     1  DC차데모/AC3상/DC콤보      255.70  127.768300  34.984695  
10    급속        50KW     1  DC차데모/AC3상/DC콤보      255.70  127.587542  34.970164  
11    급속  100KW 동시충전     2             DC콤보      255.70  127.587542  34.970164  
12    급속        50KW     1  DC차데모/AC3상/DC콤보      255.70  127.698619  34.936225  
13    급속  200KW 동시충전     2             DC콤보      255.70  127.699739  34.938525  
14    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.694138  34.928488  
15    급속         NaN     2  DC차데모/AC3상/DC콤보      191.73  127.692320  34.952065  
16    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.692992  34.936355  
17    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.697259  34.934237  
18    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.695222  34.934223  
19    급속         NaN     2  DC차데모/AC3상/DC콤보      191.73  127.690686  34.933274  
20    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.691866  34.956315  
21    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.612698  34.970095  
22    급속         NaN     1  DC차데모/AC3상/DC콤보      191.73  127.610457  34.968399

In [ ]:
# 하나의 군집에서 가장 큰 '인구분포_자동차등록_전기차'값이 동일한 경우가 존재.
#3번째 군집의 인덱스 3과 4, 10번째 군집의 인덱스 11과 12, 13번째 군집의 인덱스 15와 16 


m2 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(행정경계).add_to(m2)

for i in [3,4]:    #'급속_new_df'에서 인덱스 3과 4 
    sub_lat = 급속_new_df.loc[i,"lat"]
    sub_lon = 급속_new_df.loc[i,'lon']
    title = 급속_new_df.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='red', radius=5, tooltip=title).add_to(m2)    
for i in [11,12]:    #'급속_new_df'에서 인덱스 11과 12
    sub_lat = 급속_new_df.loc[i,"lat"]
    sub_lon = 급속_new_df.loc[i,'lon']
    title = 급속_new_df.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='purple', radius=5, tooltip=title).add_to(m2)    
for i in [15,16]:    #'급속_new_df'에서 인덱스 15와 16
    sub_lat = 급속_new_df.loc[i,"lat"]
    sub_lon = 급속_new_df.loc[i,'lon']
    title = 급속_new_df.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='green', radius=5, tooltip=title).add_to(m2)    
    
    
#'급속_new_df'에서 인덱스 3,4,11,12,15,16을 제외한 나머지
lst = []
for i in range(20):
    if (i == 3) or (i==4) or (i==11) or (i==12) or (i==15) or (i==16):
        pass
    else:
        lst.append(i)
        
for i in lst:   
    sub_lat = 급속_new_df.loc[i,"lat"]
    sub_lon = 급속_new_df.loc[i,'lon']
    title = 급속_new_df.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='blue', radius=5, tooltip=title).add_to(m2)      
    
#현재 설치되어있는 급속충전기    
for i in range(len(설치된_급속충전기)):
    sub_lat = 설치된_급속충전기.loc[i,"lat"]
    sub_lon = 설치된_급속충전기.loc[i,'lon']
    title = 설치된_급속충전기.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='yellow', radius=5, tooltip=title).add_to(m2)
        
m2

In [ ]:
# 군집3의 인덱스 3과 4비교(빨강) : 접근성이 좋은 인덱스3으로 선정
# 군집10의 인덱스 11과 12비교(보라) : 인덱스12는 산업단지 안에 위치하므로 인덱스11로 선정. 
# 군집13의 인덱스 15와 16비교(초록) : 인덱스16 주변에 건물(농협)이 있으므로 인덱스 16으로 선정. 
급속_new_df.drop([급속_new_df.index[4], 급속_new_df.index[12],급속_new_df.index[15]], inplace=True)
급속_new_df.reset_index(drop=True, inplace=True)
급속_new_df

area   주차면수         lon        lat category  소유주체 급속/완속  완속충전기_설치가능여부  \
0   1449.00   48.0  127.700269  34.939377      주차장     1    급속           0.0   
1   4702.00  135.0  127.599294  35.101532      주차장     1    급속           1.0   
2    409.00   27.0  127.583395  34.973645      주차장     1    급속           0.0   
3   4300.00   65.0  127.758582  34.979305      주차장     1    급속           1.0   
4     14.06    0.0  127.683919  35.136115     공공시설     1    급속           0.0   
5    762.00   15.0  127.721717  34.960730      주차장     1    급속           0.0   
6    827.00   30.0  127.676139  35.090000      주차장     1    급속           0.0   
7    615.00   22.0  127.640598  34.911785      주차장     1    급속           0.0   
8   1251.00   42.0  127.607064  34.974007      주차장     1    급속           0.0   
9    712.00   22.0  127.755977  34.943044      주차장     1    급속           0.0   
10   688.00   20.0  127.715877  34.974770      주차장     1    급속           0.0   
11   185.00    4.0  127.576992  34.943998      주차장     1    급속           0.0   
12   720.00   30.0  127.617527  35.068381      주차장     1    급속           0.0   
13   713.00   22.0  127.760665  34.977087      주차장     1    급속           0.0   
14  1313.00   44.0  127.698495  34.926713      주차장     1    급속           0.0   
15  2692.00   87.0  127.606442  34.942614      주차장     1    급속           1.0   
16  1970.00   66.0  127.576642  34.974388      주차장     1    급속           1.0   
17    36.00    0.0  127.762758  34.902292     공공시설     1    급속           0.0   
18  3486.00   94.0  127.564633  35.079183      주차장     1    급속           1.0   
19   622.00   22.0  127.678230  34.933951      주차장     1    급속           0.0   

        인구분포   자동차등록현황 administration    전기차증가량                    geometry  \
0  -0.243195 -0.125650            중마동 -0.162234  POINT (127.70027 34.93938)   
1  -3.792886 -4.151921            옥룡면 -0.993275  POINT (127.59929 35.10153)   
2   0.672852  0.529881            광양읍  1.262407  POINT (127.58339 34.97365)   
3   0.968742  1.305718            진월면 -1.171355  POINT (127.75858 34.97930)   
4  -8.730682 -8.726161            다압면 -1.290075  POINT (127.68392 35.13611)   
5  -0.184147 -0.167819            광영동 -0.933915  POINT (127.72172 34.96073)   
6  -2.801907 -2.881553            진상면 -1.171355  POINT (127.67614 35.09000)   
7   0.352775  0.462582            골약동 -1.290075  POINT (127.64060 34.91179)   
8   0.080942  0.161326            광양읍  1.262407  POINT (127.60706 34.97401)   
9   1.380898  1.681638            태인동 -1.290075  POINT (127.75598 34.94304)   
10 -0.436233 -0.317800            옥곡면 -1.111995  POINT (127.71588 34.97477)   
11  1.172016  0.844572            광양읍  1.262407  POINT (127.57699 34.94400)   
12 -2.057373 -2.160953            옥룡면 -0.993275  POINT (127.61753 35.06838)   
13  0.588708  0.892282            진월면 -1.171355  POINT (127.76066 34.97709)   
14 -0.026080  0.103988            중마동 -0.162234  POINT (127.69850 34.92671)   
15  0.303014  0.434911            광양읍  1.262407  POINT (127.60644 34.94261)   
16  0.759417  0.388829            광양읍  1.262407  POINT (127.57664 34.97439)   
17  1.568052  2.171627            금호동 -0.755835  POINT (127.76276 34.90229)   
18 -3.541354 -3.917943            봉강면 -1.052635  POINT (127.56463 35.07918)   
19 -0.289915 -0.173104            골약동 -1.290075  POINT (127.67823 34.93395)   

    인구분포_자동차등록_전기차  군집  
0              125   0  
1               10   1  
2              226   2  
3              273   3  
4                1   4  
5              113   5  
6               24   6  
7              171   7  
8              156   8  
9              289   9  
10              47  10  
11             286  11  
12              26  12  
13             214  13  
14             141  14  
15             170  15  
16             191  16  
17             290  17  
18              19  18  
19             101  19

In [ ]:
급속_최종 = 급속_new_df.copy()

map_급속 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(행정경계).add_to(map_급속)

for i in range(len(급속_최종)):
    sub_lat = 급속_최종.loc[i,"lat"]
    sub_lon = 급속_최종.loc[i,'lon']
    title = str(i) + " " + str(급속_최종['administration'][i])
    
    folium.CircleMarker([sub_lat, sub_lon], color='red',radius=5,tooltip=title).add_to(map_급속)

map_급속

In [ ]:
map_급속.save('급속_최종.html')

### 2) 완속충전기

#### 인덱스끼리 '인구분포', '자동차등록현황','전기차증가량'컬럼값을 비교하여 세 값 중 두 개의 값이 큰 인덱스의 count값을 1씩 증가하여 최종적으로 sort_list에 그 값을 담음

In [ ]:
완속충전기_정렬= 완속충전기[['인구분포','자동차등록현황','전기차증가량']]
human=list(완속충전기_정렬['인구분포'])
car=list(완속충전기_정렬['자동차등록현황'])
eleccar=list(완속충전기_정렬['전기차증가량'])

sort_list=[]
for i in range(len(human)):
    sort_list.append(0)

def weight_count(idx1, idx2):
    _num1 = 0
    _num2 = 0
    _listnm=[human, car, eleccar]
    for _list in _listnm:
        if _list[_sort] > _list[_sort2]:
            _num1+=1
        elif _list[_sort] == _list[_sort2]:
            pass
        else:
            _num2+=1
    return _num1, _num2

_num=0
for _sort in range(0, len(human)):
    for _sort2 in range(_sort+1, len(human)):
        _num1, _num2 = weight_count(_sort,_sort2)
        if _num1> _num2:
            sort_list[_num]+=1
        elif _num1 == _num2:
            pass
        else:
            if _num<=len(완속충전기)-1:
                sort_list[_sort2]+=1
    _num+=1

print(sort_list)

[338, 172, 326, 361, 356, 322, 301, 298, 270, 275, 281, 283, 303, 312, 140, 106, 148, 80, 206, 187, 149, 167, 94, 257, 80, 149, 194, 184, 122, 147, 190, 231, 228, 80, 103, 278, 136, 125, 394, 355, 384, 245, 147, 252, 17, 16, 18, 400, 404, 2, 7, 288, 55, 7, 2, 5, 1, 0, 12, 115, 10, 399, 146, 280, 310, 303, 285, 236, 233, 384, 20, 144, 30, 311, 403, 9, 6, 2, 174, 84, 133, 409, 175, 90, 301, 356, 172, 140, 80, 106, 135, 279, 322, 194, 286, 280, 19, 270, 361, 288, 355, 336, 143, 277, 314, 281, 232, 234, 282, 288, 287, 403, 407, 410, 310, 343, 375, 221, 290, 314, 326, 14, 13, 11, 23, 156, 164, 163, 160, 166, 149, 154, 151, 151, 153, 177, 190, 182, 125, 132, 128, 130, 133, 134, 135, 128, 126, 137, 139, 120, 112, 109, 120, 111, 115, 106, 102, 95, 92, 92, 100, 94, 80, 94, 90, 80, 100, 80, 80, 74, 67, 64, 80, 80, 69, 69, 69, 60, 60, 69, 166, 163, 151, 148, 146, 158, 159, 164, 170, 187, 176, 170, 168, 176, 154, 153, 180, 180, 176, 170, 190, 202, 200, 195, 195, 189, 195, 205, 204, 213, 203, 193, 

In [ ]:
완속충전기['인구분포_자동차등록_전기차']=sort_list
완속충전기

area   주차면수         lon        lat category 소유주체 급속/완속  \
0     4189.000  161.0  127.586883  34.970324      주차장    1  None   
1     2968.000  125.0  127.695428  34.936252      주차장    1  None   
2     2836.000   89.0  127.584586  34.975637      주차장    1  None   
3     1980.000   52.0  127.580683  34.970130      주차장    1  None   
4     1970.000   64.0  127.580707  34.972523      주차장    1  None   
..         ...    ...         ...        ...      ...  ...   ...   
406    811.780  207.0  127.565805  34.969112       주거    2  None   
407    802.080  207.0  127.563863  34.969020       주거    2  None   
408    631.195   65.0  127.699912  34.990774       주거    2  None   
409    121.290   83.0  127.589988  34.975036       주거    0  None   
410  43124.350  626.0  127.566398  34.962620     쇼핑센터    2  None   

     완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0             1.0  0.652892  0.607904            광양읍  1.262407   
1             1.0 -0.278347 -0.157118            중마동 -0.162234   
2             1.0  0.597602  0.481367            광양읍  1.262407   
3             1.0  0.803955  0.568861            광양읍  1.262407   
4             1.0  0.774028  0.561439            광양읍  1.262407   
..            ...       ...       ...            ...       ...   
406           1.0  0.745944  0.496053            광양읍  1.262407   
407           1.0  0.699774  0.345523            광양읍  1.262407   
408           1.0 -0.576433 -0.413918            옥곡면 -1.111995   
409           1.0  0.549710  0.459291            광양읍  1.262407   
410           1.0  0.869954  0.519449            광양읍  1.262407   

                       geometry  인구분포_자동차등록_전기차  
0    POINT (127.58688 34.97032)             338  
1    POINT (127.69543 34.93625)             172  
2    POINT (127.58459 34.97564)             326  
3    POINT (127.58068 34.97013)             361  
4    POINT (127.58071 34.97252)             356  
..                          ...             ...  
406  POINT (127.56580 34.96911)             353  
407  POINT (127.56386 34.96902)             301  
408  POINT (127.69991 34.99077)              15  
409  POINT (127.58999 34.97504)             311  
410  POINT (127.56640 34.96262)             362  

[411 rows x 14 columns]

#### kmeans군집화에 '인구분포','자동차등록현황','전기차증가량' 세 개의 컬럼을 넣고 20개의 군집으로 나타내기 위해 n_clusters를 20으로 설정

In [ ]:
x_완속 = 완속충전기[['인구분포','자동차등록현황','전기차증가량']]

kmeans_완속 = KMeans(n_clusters = 20, init='k-means++', max_iter=300, random_state=0)
kmeans_완속.fit(x_완속)

predict_완속 = pd.DataFrame(kmeans_완속.predict(x_완속))
predict_완속.columns=['군집']


#각 군집에 해당하는 인덱스를 '완속_index' 리스트에 넣음
완속_index=[[] for _ in range(20)]
for i in range(len(완속충전기)):
    _tmp2=predict_완속.iloc[i][0]
    완속_index[_tmp2].append(i)

    
완속_list = []
for i in range(20):
    df = 완속충전기.iloc[완속_index[i]]  #각 군집의 인덱스에 해당하는 데이터프레임 생성
    max_df = df[df.인구분포_자동차등록_전기차==max(df.인구분포_자동차등록_전기차)]     #각 군집에서 '인구분포_자동차등록_전기차'값이 가장 큰 행 추출
    max_df['군집'] = i
    완속_list.append(max_df)
    
완속_new_df = pd.concat(완속_list)
완속_new_df['급속/완속'] = '완속'
완속_new_df.reset_index(drop=True, inplace=True)
완속_new_df

area     주차면수         lon        lat category 소유주체 급속/완속  \
0      3400.000    130.0  127.696358  34.926003      주차장    1    완속   
1       520.560     67.0  127.582972  34.967211       주거    2    완속   
2      3486.000     94.0  127.564633  35.079183      주차장    1    완속   
3       378.860    102.0  127.716855  34.932853       주거    2    완속   
4       372.640    102.0  127.717363  34.933663       주거    2    완속   
5      1859.000     62.0  127.605565  34.974053      주차장    0    완속   
6      3762.000    102.0  127.756246  34.945585      주차장    0    완속   
7      4159.570    173.0  127.696864  34.934449       주거    2    완속   
8      1545.000     52.0  127.722690  34.952908      주차장    0    완속   
9      2836.000     89.0  127.584586  34.975637      주차장    1    완속   
10     2657.000     86.0  127.584608  34.975629      주차장    1    완속   
11   425821.000   1419.0  127.631555  35.069553      야영장    0    완속   
12  3293527.000  10978.0  127.591184  35.054216      야영장    1    완속   
13      475.920     73.0  127.741696  34.942963       주거    2    완속   
14      680.780    220.0  127.693011  34.941613       주거    2    완속   
15      507.104     94.0  127.572904  34.963309       주거    2    완속   
16     2684.000     87.0  127.647274  34.942971      주차장    1    완속   
17     2897.000     93.0  127.596287  34.974094      주차장    2    완속   
18     4422.000     94.0  127.586976  34.936647      주차장    2    완속   
19     5511.000    184.0  127.564926  34.960047      주차장    0    완속   
20     4702.000    135.0  127.599294  35.101532      주차장    1    완속   
21     1212.000     60.0  127.613417  35.070673      주차장    1    완속   

    완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0            1.0 -0.039080  0.079378            중마동 -0.162234   
1            1.0  0.787006  0.680616            광양읍  1.262407   
2            1.0 -3.541354 -3.917943            봉강면 -1.052635   
3            1.0  0.184136  0.155756            금호동 -0.755835   
4            1.0  0.191969  0.147938            금호동 -0.755835   
5            1.0  0.117269  0.236668            광양읍  1.262407   
6            1.0  1.344160  1.636653            태인동 -1.290075   
7            1.0 -0.220904 -0.106608            중마동 -0.162234   
8            1.0 -0.159621 -0.167708            광영동 -0.933915   
9            1.0  0.597602  0.481367            광양읍  1.262407   
10           1.0  0.597602  0.481367            광양읍  1.262407   
11           1.0 -1.140913 -1.360366            옥룡면 -0.993275   
12           1.0 -2.855074 -3.033677            옥룡면 -0.993275   
13           1.0  0.536018  0.732349            태인동 -1.290075   
14           1.0 -0.323771 -0.220260            중마동 -0.162234   
15           1.0  1.017648  0.690750            광양읍  1.262407   
16           1.0 -0.314894 -0.168811            골약동 -1.290075   
17           1.0  0.383931  0.451552            광양읍  1.262407   
18           1.0  1.371977  1.392664            광양읍  1.262407   
19           1.0  0.812393  0.448814            광양읍  1.262407   
20           1.0 -3.792886 -4.151921            옥룡면 -0.993275   
21           1.0 -2.251201 -2.435265            옥룡면 -0.993275   

                      geometry  인구분포_자동차등록_전기차  군집  
0   POINT (127.69636 34.92600)             257   0  
1   POINT (127.58297 34.96721)             376   1  
2   POINT (127.56463 35.07918)               9   2  
3   POINT (127.71686 34.93285)             273   3  
4   POINT (127.71736 34.93366)             273   3  
5   POINT (127.60557 34.97405)             277   4  
6   POINT (127.75625 34.94559)             409   5  
7   POINT (127.69686 34.93445)             218   6  
8   POINT (127.72269 34.95291)             175   7  
9   POINT (127.58459 34.97564)             326   8  
10  POINT (127.58461 34.97563)             326   8  
11  POINT (127.63156 35.06955)              13   9  
12  POINT (127.59118 35.05422)              11  10  
13  POINT (127.74170 34.94296)             312  11  
14  POINT (127.69301 34.94161)             135  12  
15  POINT (127.57290 34.96331)   

In [ ]:
# 인덱스 9와10은 여러 주차장 데이터를 합치면서 생긴 중복된 데이터임. 둘 중 하나를 제거해줌

완속_new_df.drop([완속_new_df.index[9]], inplace=True)
완속_new_df.reset_index(drop=True, inplace=True)
완속_new_df

area     주차면수         lon        lat category 소유주체 급속/완속  \
0      3400.000    130.0  127.696358  34.926003      주차장    1    완속   
1       520.560     67.0  127.582972  34.967211       주거    2    완속   
2      3486.000     94.0  127.564633  35.079183      주차장    1    완속   
3       378.860    102.0  127.716855  34.932853       주거    2    완속   
4       372.640    102.0  127.717363  34.933663       주거    2    완속   
5      1859.000     62.0  127.605565  34.974053      주차장    0    완속   
6      3762.000    102.0  127.756246  34.945585      주차장    0    완속   
7      4159.570    173.0  127.696864  34.934449       주거    2    완속   
8      1545.000     52.0  127.722690  34.952908      주차장    0    완속   
9      2657.000     86.0  127.584608  34.975629      주차장    1    완속   
10   425821.000   1419.0  127.631555  35.069553      야영장    0    완속   
11  3293527.000  10978.0  127.591184  35.054216      야영장    1    완속   
12      475.920     73.0  127.741696  34.942963       주거    2    완속   
13      680.780    220.0  127.693011  34.941613       주거    2    완속   
14      507.104     94.0  127.572904  34.963309       주거    2    완속   
15     2684.000     87.0  127.647274  34.942971      주차장    1    완속   
16     2897.000     93.0  127.596287  34.974094      주차장    2    완속   
17     4422.000     94.0  127.586976  34.936647      주차장    2    완속   
18     5511.000    184.0  127.564926  34.960047      주차장    0    완속   
19     4702.000    135.0  127.599294  35.101532      주차장    1    완속   
20     1212.000     60.0  127.613417  35.070673      주차장    1    완속   

    완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0            1.0 -0.039080  0.079378            중마동 -0.162234   
1            1.0  0.787006  0.680616            광양읍  1.262407   
2            1.0 -3.541354 -3.917943            봉강면 -1.052635   
3            1.0  0.184136  0.155756            금호동 -0.755835   
4            1.0  0.191969  0.147938            금호동 -0.755835   
5            1.0  0.117269  0.236668            광양읍  1.262407   
6            1.0  1.344160  1.636653            태인동 -1.290075   
7            1.0 -0.220904 -0.106608            중마동 -0.162234   
8            1.0 -0.159621 -0.167708            광영동 -0.933915   
9            1.0  0.597602  0.481367            광양읍  1.262407   
10           1.0 -1.140913 -1.360366            옥룡면 -0.993275   
11           1.0 -2.855074 -3.033677            옥룡면 -0.993275   
12           1.0  0.536018  0.732349            태인동 -1.290075   
13           1.0 -0.323771 -0.220260            중마동 -0.162234   
14           1.0  1.017648  0.690750            광양읍  1.262407   
15           1.0 -0.314894 -0.168811            골약동 -1.290075   
16           1.0  0.383931  0.451552            광양읍  1.262407   
17           1.0  1.371977  1.392664            광양읍  1.262407   
18           1.0  0.812393  0.448814            광양읍  1.262407   
19           1.0 -3.792886 -4.151921            옥룡면 -0.993275   
20           1.0 -2.251201 -2.435265            옥룡면 -0.993275   

                      geometry  인구분포_자동차등록_전기차  군집  
0   POINT (127.69636 34.92600)             257   0  
1   POINT (127.58297 34.96721)             376   1  
2   POINT (127.56463 35.07918)               9   2  
3   POINT (127.71686 34.93285)             273   3  
4   POINT (127.71736 34.93366)             273   3  
5   POINT (127.60557 34.97405)             277   4  
6   POINT (127.75625 34.94559)             409   5  
7   POINT (127.69686 34.93445)             218   6  
8   POINT (127.72269 34.95291)             175   7  
9   POINT (127.58461 34.97563)             326   8  
10  POINT (127.63156 35.06955)              13   9  
11  POINT (127.59118 35.05422)              11  10  
12  POINT (127.74170 34.94296)             312  11  
13  POINT (127.69301 34.94161)             135  12  
14  POINT (127.57290 34.96331)             404  13  
15  POINT (127.64727 34.94297)             135  14  
16  POINT (127.59629 34.97409)             288  15  
17  POINT (127.58698 34.93665)             410  16  
18  POINT 

In [ ]:
#현재 설치되어있는 완속충전기를 지도에 매핑하기 위해 데이터 전처리

설치된_완속충전기 = 충전기[충전기['급속/완속']=='완속']
설치된_완속충전기.reset_index(drop=True, inplace=True)
설치된_완속충전기

충전소명                                          충전소위치  \
0        광양송보파인빌5차아파트  전남 광양시 진등길 55-5 (마동 송보파인빌류 아파트) 501동~506동 상가동   
1           광양시 모리스모텔                         전남 광양시 광영로 118-1 지상주차장   
2          광양시 백운쇼핑센타                            전남 광양시 폭포사랑길 99 주차장   
3    광양시 블루핸즈(광양정비센터)                       전남 광양시 광양읍 해광로 888 실외주차장   
4            광양시 비치모텔                        전남 광양시 진월면 백운1로 389 주차장   
5   광양시 포스코 ICT 광양사업소                             전남 광양시 태인4길 20 주차장   
6           광양시 프라자모텔                                  전남 광양시 광영로 34   
7          광양시 광양읍사무소                               전남 광양시 광양읍 남등길 6   
8         광양시 광영동주민센터                                 전남 광양시 정수2길 47   
9          광양시 옥곡면사무소                             전남 광양시 옥곡면 옥진로 656   
10          광양주공이차아파트                    전남 광양시 구마9길 11(중동 중마2주공아파트)   
11          광영동 가야아파트                      전남 광양시 가야로 380(광영동 가야아파트)   
12          구산칠성이편한세상               전남 광양시 광양읍 서북2길 115(구산리 칠성이편한세상)   
13       대광로제비앙2차 아파트                       전남 광양시 진등3길 6 지하주차장 B1구역   
14               마틴모텔                        전남 광양시 새미골길 8-5 마틴모텔주차장   
15        쉐보레동광양지점서비스                       전남 광양시 김시식지1길 1-18 외부주차장   
16               호텔자바                            전남 광양시 중동로 98 지하주차장   
17         광양중마호반리젠시빌            전남 광양시 공영로 39 실내지하 101103동 사이 지하주차장   
18       송보파인빌 7차 아파트             전남 광양시 광양읍 와룡길 33 705동 707동 사이 주차장   
19          남해오네뜨 아파트          전남 광양시 광양읍 와룡길 43 실내지하 109동 지하주차장 c15   
20       광양읍 목성 주공아파트                전남 광양시 신재로 82 실외노출 관리사무소 뒷편 주차장   

      충전기 운영기관 급속/완속  충전기용량  이용대수 충전기타입  요금정보(원/kw)         lon        lat  
0          케이티    완속  7kw/h     5  AC완속      170.00  127.689013  34.953759  
1          차지비    완속  7kw/h     2  AC완속      250.00  127.716708  34.964032  
2          차지비    완속  7kw/h     2  AC완속      245.00  127.732440  34.940444  
3          차지비    완속  7kw/h     1  AC완속      245.00  127.582443  34.963334  
4          차지비    완속  7kw/h     2  AC완속      250.00  127.750981  34.962506  
5          차지비    완속  7kw/h     1  AC완속      250.00  127.760072  34.941198  
6          차지비    완속  7kw/h     2  AC완속      250.00  127.725127  34.962147  
7   한국전기차충전서비스    완속  7kw/h     1  AC완속      255.70  127.580612  34.973057  
8   한국전기차충전서비스    완속  7kw/h     1  AC완속      255.70  127.721913  34.962806  
9   한국전기차충전서비스    완속  7kw/h     1  AC완속      255.70  127.699053  34.989479  
10         케이티    완속  7kw/h     1  AC완속      170.00  127.685670  34.944650  
11         케이티    완속  7kw/h     4  AC완속      170.00  127.714850  34.966210  
12         케이티    완속  7kw/h     2  AC완속      170.00  127.576134  34.974887  
13         케이티    완속  7kw/h     3  AC완속      170.00  127.688809  34.952244  
14  한국전기차충전서비스    완속  7kw/h     2  AC완속      255.70  127.723417  34.962668  
15  한국전기차충전서비스    완속  7kw/h     1  AC완속      255.70  127.758109  34.946130  
16  한국전기차충전서비스    완속  7kw/h     2  AC완속      255.70  127.699228  34.941020  
17        한국전력    완속  7kw/h     3  AC완속      191.73  127.692992  34.936355  
18        한국전력    완속  7kw/h     2  AC완속      191.73  127.612698  34.970095  
19        한국전력    완속  7kw/h     3  AC완속      191.73  127.610457  34.968399  
20        한국전력    완속  7kw/h     2  AC완속      191.73  127.591137  34.978306

In [ ]:
# 하나의 군집에서 가장 큰 '인구분포_자동차등록_전기차'값이 동일한 경우가 존재.
#3번째 군집의 인덱스 3과 4

m3 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(행정경계).add_to(m3)

# 인덱스 3,4를 빨간색으로 마킹
for i in [3,4]:    
    sub_lat = 완속_new_df.loc[i,"lat"]
    sub_lon = 완속_new_df.loc[i,'lon']
    title = 완속_new_df.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='red', radius=5, tooltip=title).add_to(m3)

#인덱스 3,4를 제외한 나머지는 파란색으로 마킹
lst = []
for i in range(20):
    if (i==3) or (i==4):
        pass
    else:
        lst.append(i)
for i in lst:    
    sub_lat = 완속_new_df.loc[i,"lat"]
    sub_lon = 완속_new_df.loc[i,'lon']
    title = 완속_new_df.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='blue', radius=5, tooltip=title).add_to(m3)
    

#현재 설치되어있는 완속충전기는 노란색으로 마킹
for i in range(len(설치된_완속충전기)):
    sub_lat = 설치된_완속충전기.loc[i,"lat"]
    sub_lon = 설치된_완속충전기.loc[i,'lon']
    title = 설치된_완속충전기.index[i]
    folium.CircleMarker([sub_lat, sub_lon], color='yellow', radius=5, tooltip=title).add_to(m3)
    
    
m3

In [ ]:
# 군집3의 인덱스 3과 4를 비교(빨강) : 큰 도로(제철로)와 가까운 인덱스3으로 선정
완속_new_df.drop([완속_new_df.index[4]], inplace=True)
완속_new_df.reset_index(drop=True, inplace=True)
완속_new_df

area     주차면수         lon        lat category 소유주체 급속/완속  \
0      3400.000    130.0  127.696358  34.926003      주차장    1    완속   
1       520.560     67.0  127.582972  34.967211       주거    2    완속   
2      3486.000     94.0  127.564633  35.079183      주차장    1    완속   
3       378.860    102.0  127.716855  34.932853       주거    2    완속   
4      1859.000     62.0  127.605565  34.974053      주차장    0    완속   
5      3762.000    102.0  127.756246  34.945585      주차장    0    완속   
6      4159.570    173.0  127.696864  34.934449       주거    2    완속   
7      1545.000     52.0  127.722690  34.952908      주차장    0    완속   
8      2657.000     86.0  127.584608  34.975629      주차장    1    완속   
9    425821.000   1419.0  127.631555  35.069553      야영장    0    완속   
10  3293527.000  10978.0  127.591184  35.054216      야영장    1    완속   
11      475.920     73.0  127.741696  34.942963       주거    2    완속   
12      680.780    220.0  127.693011  34.941613       주거    2    완속   
13      507.104     94.0  127.572904  34.963309       주거    2    완속   
14     2684.000     87.0  127.647274  34.942971      주차장    1    완속   
15     2897.000     93.0  127.596287  34.974094      주차장    2    완속   
16     4422.000     94.0  127.586976  34.936647      주차장    2    완속   
17     5511.000    184.0  127.564926  34.960047      주차장    0    완속   
18     4702.000    135.0  127.599294  35.101532      주차장    1    완속   
19     1212.000     60.0  127.613417  35.070673      주차장    1    완속   

    완속충전기_설치가능여부      인구분포   자동차등록현황 administration    전기차증가량  \
0            1.0 -0.039080  0.079378            중마동 -0.162234   
1            1.0  0.787006  0.680616            광양읍  1.262407   
2            1.0 -3.541354 -3.917943            봉강면 -1.052635   
3            1.0  0.184136  0.155756            금호동 -0.755835   
4            1.0  0.117269  0.236668            광양읍  1.262407   
5            1.0  1.344160  1.636653            태인동 -1.290075   
6            1.0 -0.220904 -0.106608            중마동 -0.162234   
7            1.0 -0.159621 -0.167708            광영동 -0.933915   
8            1.0  0.597602  0.481367            광양읍  1.262407   
9            1.0 -1.140913 -1.360366            옥룡면 -0.993275   
10           1.0 -2.855074 -3.033677            옥룡면 -0.993275   
11           1.0  0.536018  0.732349            태인동 -1.290075   
12           1.0 -0.323771 -0.220260            중마동 -0.162234   
13           1.0  1.017648  0.690750            광양읍  1.262407   
14           1.0 -0.314894 -0.168811            골약동 -1.290075   
15           1.0  0.383931  0.451552            광양읍  1.262407   
16           1.0  1.371977  1.392664            광양읍  1.262407   
17           1.0  0.812393  0.448814            광양읍  1.262407   
18           1.0 -3.792886 -4.151921            옥룡면 -0.993275   
19           1.0 -2.251201 -2.435265            옥룡면 -0.993275   

                      geometry  인구분포_자동차등록_전기차  군집  
0   POINT (127.69636 34.92600)             257   0  
1   POINT (127.58297 34.96721)             376   1  
2   POINT (127.56463 35.07918)               9   2  
3   POINT (127.71686 34.93285)             273   3  
4   POINT (127.60557 34.97405)             277   4  
5   POINT (127.75625 34.94559)             409   5  
6   POINT (127.69686 34.93445)             218   6  
7   POINT (127.72269 34.95291)             175   7  
8   POINT (127.58461 34.97563)             326   8  
9   POINT (127.63156 35.06955)              13   9  
10  POINT (127.59118 35.05422)              11  10  
11  POINT (127.74170 34.94296)             312  11  
12  POINT (127.69301 34.94161)             135  12  
13  POINT (127.57290 34.96331)             404  13  
14  POINT (127.64727 34.94297)             135  14  
15  POINT (127.59629 34.97409)             288  15  
16  POINT (127.58698 34.93665)             410  16  
17  POINT (127.56493 34.96005)             343  17  
18  POINT (127.59929 35.10153)               1  18  
19  POINT (127.61342 35.07067)              12  19

In [ ]:
완속_최종 = 완속_new_df.copy()

map_완속 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(행정경계).add_to(map_완속)

for i in range(len(완속_최종)):
    sub_lat = 완속_최종.loc[i,"lat"]
    sub_lon = 완속_최종.loc[i,'lon']
    title = str(i) + " " + str(완속_최종['administration'][i])
    
    folium.CircleMarker([sub_lat, sub_lon], color='red',radius=5,tooltip=title).add_to(map_완속)

map_완속

In [ ]:
map_완속.save('완속_최종.html')

### 3) 최종 급속충전기와 완속충전기 

In [ ]:
최종 = pd.concat([급속_최종,완속_최종], ignore_index=True)
최종 = 최종[['lon','lat','급속/완속']]      
최종.rename(columns={'lon':'X좌표(경도)', 'lat':'Y좌표(위도)','급속/완속':'충전소구분'}, inplace=True)
최종

X좌표(경도)    Y좌표(위도) 충전소구분
0   127.700269  34.939377    급속
1   127.599294  35.101532    급속
2   127.583395  34.973645    급속
3   127.758582  34.979305    급속
4   127.683919  35.136115    급속
5   127.721717  34.960730    급속
6   127.676139  35.090000    급속
7   127.640598  34.911785    급속
8   127.607064  34.974007    급속
9   127.755977  34.943044    급속
10  127.715877  34.974770    급속
11  127.576992  34.943998    급속
12  127.617527  35.068381    급속
13  127.760665  34.977087    급속
14  127.698495  34.926713    급속
15  127.606442  34.942614    급속
16  127.576642  34.974388    급속
17  127.762758  34.902292    급속
18  127.564633  35.079183    급속
19  127.678230  34.933951    급속
20  127.696358  34.926003    완속
21  127.582972  34.967211    완속
22  127.564633  35.079183    완속
23  127.716855  34.932853    완속
24  127.605565  34.974053    완속
25  127.756246  34.945585    완속
26  127.696864  34.934449    완속
27  127.722690  34.952908    완속
28  127.584608  34.975629    완속
29  127.631555  35.069553    완속
30  127.591184  35.054216    완속
31  127.741696  34.942963    완속
32  127.693011  34.941613    완속
33  127.572904  34.963309    완속
34  127.647274  34.942971    완속
35  127.596287  34.974094    완속
36  127.586976  34.936647    완속
37  127.564926  34.960047    완속
38  127.599294  35.101532    완속
39  127.613417  35.070673    완속

# 3. 분석 결과

In [ ]:
map_최종 = folium.Map(location=center, zoom_start=11)
folium.GeoJson(행정경계).add_to(map_최종)

#급속충전기를 빨간색으로 표현
for i in range(20):
    sub_lat = 최종.loc[i,"Y좌표(위도)"]
    sub_lon = 최종.loc[i,'X좌표(경도)']
    title = 최종.index[i]
    
    folium.CircleMarker([sub_lat, sub_lon], color='red',radius=5,tooltip=title).add_to(map_최종)

#완속충전기를 파란색으로 표현    
for i in range(20,40):
    sub_lat = 최종.loc[i,"Y좌표(위도)"]
    sub_lon = 최종.loc[i,'X좌표(경도)']
    title = 최종.index[i]
    
    folium.CircleMarker([sub_lat, sub_lon], color='blue',radius=5,tooltip=title).add_to(map_최종)    
    
map_최종

In [ ]:
최종.to_csv("광양시_전기차충전소_위치선정.csv", index=False, encoding='cp949')